# Packages / Glovbal Variables 

In [1]:
# Importing packages 
import pandas as pd
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt
import mysql.connector
import pymysql
# from mysql.connector import Error
#%matplotlib inline

In [2]:
!pip install mysql-connector-python

In [3]:
pip install pandas sqlalchemy

Note: you may need to restart the kernel to use updated packages.


In [4]:
db_name_stag = "staging_db"
db_name_prod = "production_db"
db_host = "localhost"
db_username = "root"
db_password = "mysql"


onn = mysql.connector.connect(
    user=db_username,
    password=db_password,
    host=db_host,
    port='3306',
    database=db_name_stag)

# Data Cleaning - Pick Data

## Importing PicK_Data 

In [5]:
# Loading pick_dat from MySQL 
query = "SELECT * FROM pick_data"
pickDF = pd.read_sql(query, onn)
display(pickDF)

C:\Users\HayateSato\AppData\Local\Temp\ipykernel_12336\1201537029.py:3: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  pickDF = pd.read_sql(query, onn)


SKU WAREHOUSE_SECTION  ORIGIN ORDER_NUMBER  ORDER_POSITION  \
0         000002               SHL      48     07055448               1   
1         000002               SHL      48     07055448               1   
2         000002               SHL      48     07055448               1   
3         000002               SHL      48     07055448               1   
4         000002               SHL      48     07055448               1   
...          ...               ...     ...          ...             ...   
33888984  189976        Kabellager      48     06108542               1   
33888985  V68755               SHL      48     06108742               1   
33888986  260573               SHL      48     06108743               2   
33888987  451203               SHL      48     06108743               1   
33888988  V11016               SHL      48     06108743               3   

          PICK_VOLUME QUANTITY_UNIT           DATE_TIME  
0                  30            St 2017-06-30 11:22:35  
1                  30            St 2017-06-30 12:04:50  
2                  20            St 2017-06-30 12:04:51  
3                  30            St 2017-06-30 12:05:02  
4                  12            St 2017-06-30 12:05:12  
...               ...           ...                 ...  
33888984           30            Mt 2016-12-30 16:29:35  
33888985            1            St 2016-12-30 16:33:44  
33888986            1            St 2016-12-30 16:34:04  
33888987            1            St 2016-12-30 16:34:04  
33888988           10            St 2016-12-30 16:34:04  

[33888989 rows x 8 columns]

In [6]:
pickDF.dtypes

SKU                          object
WAREHOUSE_SECTION            object
ORIGIN                        int64
ORDER_NUMBER                 object
ORDER_POSITION                int64
PICK_VOLUME                   int64
QUANTITY_UNIT                object
DATE_TIME            datetime64[ns]
dtype: object

## Duplicates

In [7]:
# Identifying duplicated rows and counting how many we have
numRow = len(pickDF)
pickDF_Dub = pickDF[pickDF.duplicated()]
numRow_Dub = len(pickDF_Dub)
ratio_Dub = round((numRow_Dub/numRow)*100, 2)
print(f" There are {numRow_Dub} rows of rows that are duplicates")
print(f" that counts {ratio_Dub} % of the total row")

 There are 8024 rows of rows that are duplicates
 that counts 0.02 % of the total row


In [8]:
# Deleting the dupliated rows
pickDF_woDub = pickDF.drop_duplicates()

# checking if the duplicates are deleted 
numRow_woDub = len(pickDF_woDub)
print(f" There are {numRow_woDub} rows of rows left")
print(f" We deleted {numRow - numRow_woDub} rows from original dataset")

 There are 33880965 rows of rows left
 We deleted 8024 rows from original dataset


## Inconsistancies: negative & 0 pick volume

In [9]:
# Negative values 
pickDF_noDup_negaitive = pickDF_woDub[pickDF_woDub.PICK_VOLUME < 0]
numRow_nega = len(pickDF_noDup_negaitive)
ratio_nega = round((numRow_nega/numRow)*100, 4)
print(f" There are {numRow_nega} rows of rows that have negative values")
print(f" that counts {ratio_nega} % of the total row")
print("---------------------------")

# Zero values
pickDF_noDup_zero = pickDF_woDub[pickDF_woDub.PICK_VOLUME == 0]
numRow_zero = len(pickDF_noDup_zero)
ratio_zero = round((numRow_zero/numRow)*100, 2)
print(f" There are {numRow_zero} rows of rows that have pick volume of 0")
print(f" that counts {ratio_zero} % of the total row")
print("---------------------------")

# Positive values
pickDF_noDup_positive = pickDF_woDub[pickDF_woDub.PICK_VOLUME > 0]    ########## This dataset includes only posisitve values. We will use this for the process after this 
numRow_posi = len(pickDF_noDup_positive)
print(f" There are {numRow_posi} rows of rows that have positive values") 

 There are 100 rows of rows that have negative values
 that counts 0.0003 % of the total row
---------------------------
 There are 190253 rows of rows that have pick volume of 0
 that counts 0.56 % of the total row
---------------------------
 There are 33690612 rows of rows that have positive values


In [10]:
pickDF.dtypes

SKU                          object
WAREHOUSE_SECTION            object
ORIGIN                        int64
ORDER_NUMBER                 object
ORDER_POSITION                int64
PICK_VOLUME                   int64
QUANTITY_UNIT                object
DATE_TIME            datetime64[ns]
dtype: object

In [11]:
print(f"Original row : {numRow}\n Num of duplicates : {numRow_Dub}")
print("------------------------------------------------")
print(f"After deleting duplicates : {numRow_woDub} \n Num of negative pick : {numRow_nega}\n Num of zero pick : {numRow_zero}")
print("------------------------------------------------") 
print(f"After deleting negative & 0 pick : {numRow_posi}")

ratio_posi = round((numRow_posi/numRow)*100, 2)
ratio_nonPosi = round(100 - ratio_posi, 2)
print(f" in total, we deleted {ratio_nonPosi} % of row against the original dataset so far")

Original row : 33888989
 Num of duplicates : 8024
------------------------------------------------
After deleting duplicates : 33880965 
 Num of negative pick : 100
 Num of zero pick : 190253
------------------------------------------------
After deleting negative & 0 pick : 33690612
 in total, we deleted 0.59 % of row against the original dataset so far


## Calculating and finding Outliers

In [12]:
# Checking the distinct WH section and qty units
print(f"WAREHOUSE : {pd.unique(pickDF.WAREHOUSE_SECTION)}")
print(f"QTY UNIT : {pd.unique(pickDF.QUANTITY_UNIT)}")

WAREHOUSE : ['SHL' 'AKL' 'HRL' 'Manuell' 'Kabellager']
QTY UNIT : ['St' 'Mt' 'Se' 'Ro' 'Bl' 'Ei' 'Pa' 'VE' 'kg']


In [13]:
# We will handle the outliers for each Warehouse section 
# To do so, we first split the data set into 5 data sets, by warehouse section 
Pick_SHL = pickDF_noDup_positive[pickDF_noDup_positive.WAREHOUSE_SECTION == 'SHL']
Pick_AKL = pickDF_noDup_positive[pickDF_noDup_positive.WAREHOUSE_SECTION == 'AKL']
Pick_HRL = pickDF_noDup_positive[pickDF_noDup_positive.WAREHOUSE_SECTION == 'HRL']
Pick_Man = pickDF_noDup_positive[pickDF_noDup_positive.WAREHOUSE_SECTION == 'Manuell']
Pick_Kab = pickDF_noDup_positive[pickDF_noDup_positive.WAREHOUSE_SECTION == 'Kabellager']

# Then we will split these 5 data sets into 9 data sets each so each contain only single Qty Unit. 
### we will have 5 x 9 = 45 data sets 
# This way, we want to identify the extreme values when compared against the values that have the same Qty Unit and that are picked in the same warehouse. 

### SHL Wahoure

In [14]:
# We split the SHL data set into 9 data sets 
Pick_SHL_St = Pick_SHL[Pick_SHL.QUANTITY_UNIT == 'St']
Pick_SHL_Mt = Pick_SHL[Pick_SHL.QUANTITY_UNIT == 'Mt']
Pick_SHL_Se = Pick_SHL[Pick_SHL.QUANTITY_UNIT == 'Se']
Pick_SHL_Ro = Pick_SHL[Pick_SHL.QUANTITY_UNIT == 'Ro']
Pick_SHL_Bl = Pick_SHL[Pick_SHL.QUANTITY_UNIT == 'Bl']
Pick_SHL_Ei = Pick_SHL[Pick_SHL.QUANTITY_UNIT == 'Ei']
Pick_SHL_Pa = Pick_SHL[Pick_SHL.QUANTITY_UNIT == 'Pa']
Pick_SHL_VE = Pick_SHL[Pick_SHL.QUANTITY_UNIT == 'VE']
Pick_SHL_Kg = Pick_SHL[Pick_SHL.QUANTITY_UNIT == 'kg']


# Calculating the 4S boundaries 
### Normally 3S rule/3x, but here we use 4x because 3x still give a large number
# Creating a new df that does NOT contain outliers 
DF_SHL_St = Pick_SHL_St[np.abs(Pick_SHL_St.PICK_VOLUME-Pick_SHL_St.PICK_VOLUME.mean()) <= (4*Pick_SHL_St.PICK_VOLUME.std())]
DF_SHL_Mt = Pick_SHL_Mt[np.abs(Pick_SHL_Mt.PICK_VOLUME-Pick_SHL_Mt.PICK_VOLUME.mean()) <= (4*Pick_SHL_Mt.PICK_VOLUME.std())]
DF_SHL_Se = Pick_SHL_Se[np.abs(Pick_SHL_Se.PICK_VOLUME-Pick_SHL_Se.PICK_VOLUME.mean()) <= (4*Pick_SHL_Se.PICK_VOLUME.std())]
DF_SHL_Ro = Pick_SHL_Ro[np.abs(Pick_SHL_Ro.PICK_VOLUME-Pick_SHL_Ro.PICK_VOLUME.mean()) <= (4*Pick_SHL_Ro.PICK_VOLUME.std())]
DF_SHL_Bl = Pick_SHL_Bl[np.abs(Pick_SHL_Bl.PICK_VOLUME-Pick_SHL_Bl.PICK_VOLUME.mean()) <= (4*Pick_SHL_Bl.PICK_VOLUME.std())]
DF_SHL_Ei = Pick_SHL_Ei[np.abs(Pick_SHL_Ei.PICK_VOLUME-Pick_SHL_Ei.PICK_VOLUME.mean()) <= (4*Pick_SHL_Ei.PICK_VOLUME.std())]
DF_SHL_Pa = Pick_SHL_Pa[np.abs(Pick_SHL_Pa.PICK_VOLUME-Pick_SHL_Pa.PICK_VOLUME.mean()) <= (4*Pick_SHL_Pa.PICK_VOLUME.std())]
DF_SHL_VE = Pick_SHL_VE[np.abs(Pick_SHL_VE.PICK_VOLUME-Pick_SHL_VE.PICK_VOLUME.mean()) <= (4*Pick_SHL_VE.PICK_VOLUME.std())]
DF_SHL_Kg = Pick_SHL_Kg[np.abs(Pick_SHL_Kg.PICK_VOLUME-Pick_SHL_Kg.PICK_VOLUME.mean()) <= (4*Pick_SHL_Kg.PICK_VOLUME.std())]

# Creating a df that contains only outliers, by filtering out only outlier values/rows from SHL dataset. 
### in python, "~" means "not"
### so this line first checks the same value between the df_WH1_QtyUnit and df_WH1_QtyUnit_nonOutliers, 
### then ~ flips the argument, so it ends up taking all rows that are not in df_WH1_nonOutliers.
outlier_SHL_St = Pick_SHL_St[~Pick_SHL_St.index.isin(DF_SHL_St.index)]
outlier_SHL_Mt = Pick_SHL_Mt[~Pick_SHL_Mt.index.isin(DF_SHL_Mt.index)]
outlier_SHL_Se = Pick_SHL_Se[~Pick_SHL_Se.index.isin(DF_SHL_Se.index)]
outlier_SHL_Ro = Pick_SHL_Ro[~Pick_SHL_Ro.index.isin(DF_SHL_Ro.index)]
outlier_SHL_Bl = Pick_SHL_Bl[~Pick_SHL_Bl.index.isin(DF_SHL_Bl.index)]
outlier_SHL_Ei = Pick_SHL_Ei[~Pick_SHL_Ei.index.isin(DF_SHL_Ei.index)]
outlier_SHL_Pa = Pick_SHL_Pa[~Pick_SHL_Pa.index.isin(DF_SHL_Pa.index)]
outlier_SHL_VE = Pick_SHL_VE[~Pick_SHL_VE.index.isin(DF_SHL_VE.index)]
outlier_SHL_Kg = Pick_SHL_Kg[~Pick_SHL_Kg.index.isin(DF_SHL_Kg.index)]

In [15]:
outliers_SHL = pd.concat([outlier_SHL_St,outlier_SHL_Mt,outlier_SHL_Se,outlier_SHL_Ro,outlier_SHL_Bl,outlier_SHL_Ei,outlier_SHL_Pa,outlier_SHL_VE,outlier_SHL_Kg])
outliers_SHL.count()

SKU                  159617
WAREHOUSE_SECTION    159617
ORIGIN               159617
ORDER_NUMBER         159617
ORDER_POSITION       159617
PICK_VOLUME          159617
QUANTITY_UNIT        159617
DATE_TIME            159617
dtype: int64

In [16]:
print ('Range for SHL - St min: ', DF_SHL_St['PICK_VOLUME'].min(), ' , St max: ', DF_SHL_St['PICK_VOLUME'].max())
print ('Range for SHL - Mt min: ', DF_SHL_Mt['PICK_VOLUME'].min(), ' , Mt max: ', DF_SHL_Mt['PICK_VOLUME'].max())
print ('Range for SHL - Se min: ', DF_SHL_Se['PICK_VOLUME'].min(), ' , Se max: ', DF_SHL_Se['PICK_VOLUME'].max())
print ('Range for SHL - Ro min: ', DF_SHL_Ro['PICK_VOLUME'].min(), ' , Ro max: ', DF_SHL_Ro['PICK_VOLUME'].max())
print ('Range for SHL - Bl min: ', DF_SHL_Bl['PICK_VOLUME'].min(), ' , Bl max: ', DF_SHL_Bl['PICK_VOLUME'].max())
print ('Range for SHL - Ei min: ', DF_SHL_Ei['PICK_VOLUME'].min(), ' , Ei max: ', DF_SHL_Ei['PICK_VOLUME'].max())
print ('Range for SHL - Pa min: ', DF_SHL_Pa['PICK_VOLUME'].min(), ' , Pa max: ', DF_SHL_Pa['PICK_VOLUME'].max())
print ('Range for SHL - VE min: ', DF_SHL_VE['PICK_VOLUME'].min(), ' , VE max: ', DF_SHL_VE['PICK_VOLUME'].max())
print ('Range for SHL - Kg min: ', DF_SHL_Kg['PICK_VOLUME'].min(), ' , Kg max: ', DF_SHL_Kg['PICK_VOLUME'].max())

Range for SHL - St min:  1  , St max:  880
Range for SHL - Mt min:  1  , Mt max:  500
Range for SHL - Se min:  1  , Se max:  22
Range for SHL - Ro min:  1  , Ro max:  21
Range for SHL - Bl min:  1  , Bl max:  54
Range for SHL - Ei min:  nan  , Ei max:  nan
Range for SHL - Pa min:  1  , Pa max:  39
Range for SHL - VE min:  1  , VE max:  35
Range for SHL - Kg min:  nan  , Kg max:  nan


### AKL Wahoure

In [17]:
# AKL
Pick_AKL_St = Pick_AKL.loc[(Pick_AKL.QUANTITY_UNIT == 'St')]
Pick_AKL_Mt = Pick_AKL.loc[(Pick_AKL.QUANTITY_UNIT == 'Mt')]
Pick_AKL_Se = Pick_AKL.loc[(Pick_AKL.QUANTITY_UNIT == 'Se')]
Pick_AKL_Ro = Pick_AKL.loc[(Pick_AKL.QUANTITY_UNIT == 'Ro')]
Pick_AKL_Bl = Pick_AKL.loc[(Pick_AKL.QUANTITY_UNIT == 'Bl')]
Pick_AKL_Ei = Pick_AKL.loc[(Pick_AKL.QUANTITY_UNIT == 'Ei')]
Pick_AKL_Pa = Pick_AKL.loc[(Pick_AKL.QUANTITY_UNIT == 'Pa')]
Pick_AKL_VE = Pick_AKL.loc[(Pick_AKL.QUANTITY_UNIT == 'VE')]
Pick_AKL_Kg = Pick_AKL.loc[(Pick_AKL.QUANTITY_UNIT == 'kg')]

# Non-Outliers
DF_AKL_St = Pick_AKL_St[np.abs(Pick_AKL_St.PICK_VOLUME-Pick_AKL_St.PICK_VOLUME.mean()) <= (4*Pick_AKL_St.PICK_VOLUME.std())]
DF_AKL_Mt = Pick_AKL_Mt[np.abs(Pick_AKL_Mt.PICK_VOLUME-Pick_AKL_Mt.PICK_VOLUME.mean()) <= (4*Pick_AKL_Mt.PICK_VOLUME.std())]
DF_AKL_Se = Pick_AKL_Se[np.abs(Pick_AKL_Se.PICK_VOLUME-Pick_AKL_Se.PICK_VOLUME.mean()) <= (4*Pick_AKL_Se.PICK_VOLUME.std())]
DF_AKL_Ro = Pick_AKL_Ro[np.abs(Pick_AKL_Ro.PICK_VOLUME-Pick_AKL_Ro.PICK_VOLUME.mean()) <= (4*Pick_AKL_Ro.PICK_VOLUME.std())]
DF_AKL_Bl = Pick_AKL_Bl[np.abs(Pick_AKL_Bl.PICK_VOLUME-Pick_AKL_Bl.PICK_VOLUME.mean()) <= (4*Pick_AKL_Bl.PICK_VOLUME.std())]
DF_AKL_Ei = Pick_AKL_Ei[np.abs(Pick_AKL_Ei.PICK_VOLUME-Pick_AKL_Ei.PICK_VOLUME.mean()) <= (4*Pick_AKL_Ei.PICK_VOLUME.std())]
DF_AKL_Pa = Pick_AKL_Pa[np.abs(Pick_AKL_Pa.PICK_VOLUME-Pick_AKL_Pa.PICK_VOLUME.mean()) <= (4*Pick_AKL_Pa.PICK_VOLUME.std())]
DF_AKL_VE = Pick_AKL_VE[np.abs(Pick_AKL_VE.PICK_VOLUME-Pick_AKL_VE.PICK_VOLUME.mean()) <= (4*Pick_AKL_VE.PICK_VOLUME.std())]
DF_AKL_Kg = Pick_AKL_Kg[np.abs(Pick_AKL_Kg.PICK_VOLUME-Pick_AKL_Kg.PICK_VOLUME.mean()) <= (4*Pick_AKL_Kg.PICK_VOLUME.std())]

# Outliers
outlier_AKL_St = Pick_AKL_St[~Pick_AKL_St.index.isin(DF_AKL_St.index)]
outlier_AKL_Mt = Pick_AKL_Mt[~Pick_AKL_Mt.index.isin(DF_AKL_Mt.index)]
outlier_AKL_Se = Pick_AKL_Se[~Pick_AKL_Se.index.isin(DF_AKL_Se.index)]
outlier_AKL_Ro = Pick_AKL_Ro[~Pick_AKL_Ro.index.isin(DF_AKL_Ro.index)]
outlier_AKL_Bl = Pick_AKL_Bl[~Pick_AKL_Bl.index.isin(DF_AKL_Bl.index)]
outlier_AKL_Ei = Pick_AKL_Ei[~Pick_AKL_Ei.index.isin(DF_AKL_Ei.index)]
outlier_AKL_Pa = Pick_AKL_Pa[~Pick_AKL_Pa.index.isin(DF_AKL_Pa.index)]
outlier_AKL_VE = Pick_AKL_VE[~Pick_AKL_VE.index.isin(DF_AKL_VE.index)]
outlier_AKL_Kg = Pick_AKL_Kg[~Pick_AKL_Kg.index.isin(DF_AKL_Kg.index)]

In [18]:
outliers_AKL = pd.concat([outlier_AKL_St,outlier_AKL_Mt,outlier_AKL_Se,outlier_AKL_Ro,outlier_AKL_Bl,outlier_AKL_Ei,outlier_AKL_Pa,outlier_AKL_VE,outlier_AKL_Kg])
outliers_AKL.count()

SKU                  107223
WAREHOUSE_SECTION    107223
ORIGIN               107223
ORDER_NUMBER         107223
ORDER_POSITION       107223
PICK_VOLUME          107223
QUANTITY_UNIT        107223
DATE_TIME            107223
dtype: int64

In [19]:
print ('Range for AKL - St min: ', DF_AKL_St['PICK_VOLUME'].min(), ' , St max: ', DF_AKL_St['PICK_VOLUME'].max())
print ('Range for AKL - Mt min: ', DF_AKL_Mt['PICK_VOLUME'].min(), ' , Mt max: ', DF_AKL_Mt['PICK_VOLUME'].max())
print ('Range for AKL - Se min: ', DF_AKL_Se['PICK_VOLUME'].min(), ' , Se max: ', DF_AKL_Se['PICK_VOLUME'].max())
print ('Range for AKL - Ro min: ', DF_AKL_Ro['PICK_VOLUME'].min(), ' , Ro max: ', DF_AKL_Ro['PICK_VOLUME'].max())
print ('Range for AKL - Bl min: ', DF_AKL_Bl['PICK_VOLUME'].min(), ' , Bl max: ', DF_AKL_Bl['PICK_VOLUME'].max())
print ('Range for AKL - Ei min: ', DF_AKL_Ei['PICK_VOLUME'].min(), ' , Ei max: ', DF_AKL_Ei['PICK_VOLUME'].max())
print ('Range for AKL - Pa min: ', DF_AKL_Pa['PICK_VOLUME'].min(), ' , Pa max: ', DF_AKL_Pa['PICK_VOLUME'].max())
print ('Range for AKL - VE min: ', DF_AKL_VE['PICK_VOLUME'].min(), ' , VE max: ', DF_AKL_VE['PICK_VOLUME'].max())
print ('Range for AKL - Kg min: ', DF_AKL_Kg['PICK_VOLUME'].min(), ' , Kg max: ', DF_AKL_Kg['PICK_VOLUME'].max())

Range for AKL - St min:  1  , St max:  775
Range for AKL - Mt min:  1  , Mt max:  750
Range for AKL - Se min:  1  , Se max:  16
Range for AKL - Ro min:  1  , Ro max:  19
Range for AKL - Bl min:  1  , Bl max:  59
Range for AKL - Ei min:  1  , Ei max:  1
Range for AKL - Pa min:  1  , Pa max:  32
Range for AKL - VE min:  1  , VE max:  22
Range for AKL - Kg min:  nan  , Kg max:  nan


### HRL Wahoure

In [20]:
# HRL
Pick_HRL_St = Pick_HRL.loc[(Pick_HRL.QUANTITY_UNIT == 'St')]
Pick_HRL_Mt = Pick_HRL.loc[(Pick_HRL.QUANTITY_UNIT == 'Mt')]
Pick_HRL_Se = Pick_HRL.loc[(Pick_HRL.QUANTITY_UNIT == 'Se')]
Pick_HRL_Ro = Pick_HRL.loc[(Pick_HRL.QUANTITY_UNIT == 'Ro')]
Pick_HRL_Bl = Pick_HRL.loc[(Pick_HRL.QUANTITY_UNIT == 'Bl')]
Pick_HRL_Ei = Pick_HRL.loc[(Pick_HRL.QUANTITY_UNIT == 'Ei')]
Pick_HRL_Pa = Pick_HRL.loc[(Pick_HRL.QUANTITY_UNIT == 'Pa')]
Pick_HRL_VE = Pick_HRL.loc[(Pick_HRL.QUANTITY_UNIT == 'VE')]
Pick_HRL_Kg = Pick_HRL.loc[(Pick_HRL.QUANTITY_UNIT == 'kg')]

# Non-outliers
DF_HRL_St = Pick_HRL_St[np.abs(Pick_HRL_St.PICK_VOLUME-Pick_HRL_St.PICK_VOLUME.mean()) <= (4*Pick_HRL_St.PICK_VOLUME.std())]
DF_HRL_Mt = Pick_HRL_Mt[np.abs(Pick_HRL_Mt.PICK_VOLUME-Pick_HRL_Mt.PICK_VOLUME.mean()) <= (4*Pick_HRL_Mt.PICK_VOLUME.std())]
DF_HRL_Se = Pick_HRL_Se[np.abs(Pick_HRL_Se.PICK_VOLUME-Pick_HRL_Se.PICK_VOLUME.mean()) <= (4*Pick_HRL_Se.PICK_VOLUME.std())]
DF_HRL_Ro = Pick_HRL_Ro[np.abs(Pick_HRL_Ro.PICK_VOLUME-Pick_HRL_Ro.PICK_VOLUME.mean()) <= (4*Pick_HRL_Ro.PICK_VOLUME.std())]
DF_HRL_Bl = Pick_HRL_Bl[np.abs(Pick_HRL_Bl.PICK_VOLUME-Pick_HRL_Bl.PICK_VOLUME.mean()) <= (4*Pick_HRL_Bl.PICK_VOLUME.std())]
DF_HRL_Ei = Pick_HRL_Ei[np.abs(Pick_HRL_Ei.PICK_VOLUME-Pick_HRL_Ei.PICK_VOLUME.mean()) <= (4*Pick_HRL_Ei.PICK_VOLUME.std())]
DF_HRL_Pa = Pick_HRL_Pa[np.abs(Pick_HRL_Pa.PICK_VOLUME-Pick_HRL_Pa.PICK_VOLUME.mean()) <= (4*Pick_HRL_Pa.PICK_VOLUME.std())]
DF_HRL_VE = Pick_HRL_VE[np.abs(Pick_HRL_VE.PICK_VOLUME-Pick_HRL_VE.PICK_VOLUME.mean()) <= (4*Pick_HRL_VE.PICK_VOLUME.std())]
DF_HRL_Kg = Pick_HRL_Kg[np.abs(Pick_HRL_Kg.PICK_VOLUME-Pick_HRL_Kg.PICK_VOLUME.mean()) <= (4*Pick_HRL_Kg.PICK_VOLUME.std())]

# Outliers
outlier_HRL_St = Pick_HRL_St[~Pick_HRL_St.index.isin(DF_HRL_St.index)]
outlier_HRL_Mt = Pick_HRL_Mt[~Pick_HRL_Mt.index.isin(DF_HRL_Mt.index)]
outlier_HRL_Se = Pick_HRL_Se[~Pick_HRL_Se.index.isin(DF_HRL_Se.index)]
outlier_HRL_Ro = Pick_HRL_Ro[~Pick_HRL_Ro.index.isin(DF_HRL_Ro.index)]
outlier_HRL_Bl = Pick_HRL_Bl[~Pick_HRL_Bl.index.isin(DF_HRL_Bl.index)]
outlier_HRL_Ei = Pick_HRL_Ei[~Pick_HRL_Ei.index.isin(DF_HRL_Ei.index)]
outlier_HRL_Pa = Pick_HRL_Pa[~Pick_HRL_Pa.index.isin(DF_HRL_Pa.index)]
outlier_HRL_VE = Pick_HRL_VE[~Pick_HRL_VE.index.isin(DF_HRL_VE.index)]
outlier_HRL_Kg = Pick_HRL_Kg[~Pick_HRL_Kg.index.isin(DF_HRL_Kg.index)]

In [21]:
outliers_HRL = pd.concat([outlier_HRL_St,outlier_HRL_Mt,outlier_HRL_Se,outlier_HRL_Ro,outlier_HRL_Bl,outlier_HRL_Ei,outlier_HRL_Pa,outlier_HRL_VE,outlier_HRL_Kg])
outliers_HRL.count()

SKU                  18433
WAREHOUSE_SECTION    18433
ORIGIN               18433
ORDER_NUMBER         18433
ORDER_POSITION       18433
PICK_VOLUME          18433
QUANTITY_UNIT        18433
DATE_TIME            18433
dtype: int64

In [22]:
print ('Range for HRL - St min: ', DF_HRL_St['PICK_VOLUME'].min(), ' , St max: ', DF_HRL_St['PICK_VOLUME'].max())
print ('Range for HRL - Mt min: ', DF_HRL_Mt['PICK_VOLUME'].min(), ' , Mt max: ', DF_HRL_Mt['PICK_VOLUME'].max())
print ('Range for HRL - Se min: ', DF_HRL_Se['PICK_VOLUME'].min(), ' , Se max: ', DF_HRL_Se['PICK_VOLUME'].max())
print ('Range for HRL - Ro min: ', DF_HRL_Ro['PICK_VOLUME'].min(), ' , Ro max: ', DF_HRL_Ro['PICK_VOLUME'].max())
print ('Range for HRL - Bl min: ', DF_HRL_Bl['PICK_VOLUME'].min(), ' , Bl max: ', DF_HRL_Bl['PICK_VOLUME'].max())
print ('Range for HRL - Ei min: ', DF_HRL_Ei['PICK_VOLUME'].min(), ' , Ei max: ', DF_HRL_Ei['PICK_VOLUME'].max())
print ('Range for HRL - Pa min: ', DF_HRL_Pa['PICK_VOLUME'].min(), ' , Pa max: ', DF_HRL_Pa['PICK_VOLUME'].max())
print ('Range for HRL - VE min: ', DF_HRL_VE['PICK_VOLUME'].min(), ' , VE max: ', DF_HRL_VE['PICK_VOLUME'].max())
print ('Range for HRL - Kg min: ', DF_HRL_Kg['PICK_VOLUME'].min(), ' , Kg max: ', DF_HRL_Kg['PICK_VOLUME'].max())

Range for HRL - St min:  1  , St max:  3500
Range for HRL - Mt min:  1  , Mt max:  2250
Range for HRL - Se min:  1  , Se max:  7
Range for HRL - Ro min:  1  , Ro max:  40
Range for HRL - Bl min:  1  , Bl max:  250
Range for HRL - Ei min:  1  , Ei max:  10
Range for HRL - Pa min:  1  , Pa max:  48
Range for HRL - VE min:  1  , VE max:  8
Range for HRL - Kg min:  1  , Kg max:  75


### Manual Wahoure

In [23]:
# Mannual
Pick_Man_St = Pick_Man.loc[(Pick_Man.QUANTITY_UNIT == 'St')]
Pick_Man_Mt = Pick_Man.loc[(Pick_Man.QUANTITY_UNIT == 'Mt')]
Pick_Man_Se = Pick_Man.loc[(Pick_Man.QUANTITY_UNIT == 'Se')]
Pick_Man_Ro = Pick_Man.loc[(Pick_Man.QUANTITY_UNIT == 'Ro')]
Pick_Man_Bl = Pick_Man.loc[(Pick_Man.QUANTITY_UNIT == 'Bl')]
Pick_Man_Ei = Pick_Man.loc[(Pick_Man.QUANTITY_UNIT == 'Ei')]
Pick_Man_Pa = Pick_Man.loc[(Pick_Man.QUANTITY_UNIT == 'Pa')]
Pick_Man_VE = Pick_Man.loc[(Pick_Man.QUANTITY_UNIT == 'VE')]
Pick_Man_Kg = Pick_Man.loc[(Pick_Man.QUANTITY_UNIT == 'kg')]

# Non-outliers
DF_Man_St = Pick_Man_St[np.abs(Pick_Man_St.PICK_VOLUME-Pick_Man_St.PICK_VOLUME.mean()) <= (4*Pick_Man_St.PICK_VOLUME.std())]
DF_Man_Mt = Pick_Man_Mt[np.abs(Pick_Man_Mt.PICK_VOLUME-Pick_Man_Mt.PICK_VOLUME.mean()) <= (4*Pick_Man_Mt.PICK_VOLUME.std())]
DF_Man_Se = Pick_Man_Se[np.abs(Pick_Man_Se.PICK_VOLUME-Pick_Man_Se.PICK_VOLUME.mean()) <= (4*Pick_Man_Se.PICK_VOLUME.std())]
DF_Man_Ro = Pick_Man_Ro[np.abs(Pick_Man_Ro.PICK_VOLUME-Pick_Man_Ro.PICK_VOLUME.mean()) <= (4*Pick_Man_Ro.PICK_VOLUME.std())]
DF_Man_Bl = Pick_Man_Bl[np.abs(Pick_Man_Bl.PICK_VOLUME-Pick_Man_Bl.PICK_VOLUME.mean()) <= (4*Pick_Man_Bl.PICK_VOLUME.std())]
DF_Man_Ei = Pick_Man_Ei[np.abs(Pick_Man_Ei.PICK_VOLUME-Pick_Man_Ei.PICK_VOLUME.mean()) <= (4*Pick_Man_Ei.PICK_VOLUME.std())]
DF_Man_Pa = Pick_Man_Pa[np.abs(Pick_Man_Pa.PICK_VOLUME-Pick_Man_Pa.PICK_VOLUME.mean()) <= (4*Pick_Man_Pa.PICK_VOLUME.std())]
DF_Man_VE = Pick_Man_VE[np.abs(Pick_Man_VE.PICK_VOLUME-Pick_Man_VE.PICK_VOLUME.mean()) <= (4*Pick_Man_VE.PICK_VOLUME.std())]
DF_Man_Kg = Pick_Man_Kg[np.abs(Pick_Man_Kg.PICK_VOLUME-Pick_Man_Kg.PICK_VOLUME.mean()) <= (4*Pick_Man_Kg.PICK_VOLUME.std())]

# Outliers
outlier_Man_St = Pick_Man_St[~Pick_Man_St.index.isin(DF_Man_St.index)]
outlier_Man_Mt = Pick_Man_Mt[~Pick_Man_Mt.index.isin(DF_Man_Mt.index)]
outlier_Man_Se = Pick_Man_Se[~Pick_Man_Se.index.isin(DF_Man_Se.index)]
outlier_Man_Ro = Pick_Man_Ro[~Pick_Man_Ro.index.isin(DF_Man_Ro.index)]
outlier_Man_Bl = Pick_Man_Bl[~Pick_Man_Bl.index.isin(DF_Man_Bl.index)]
outlier_Man_Ei = Pick_Man_Ei[~Pick_Man_Ei.index.isin(DF_Man_Ei.index)]
outlier_Man_Pa = Pick_Man_Pa[~Pick_Man_Pa.index.isin(DF_Man_Pa.index)]
outlier_Man_VE = Pick_Man_VE[~Pick_Man_VE.index.isin(DF_Man_VE.index)]
outlier_Man_Kg = Pick_Man_Kg[~Pick_Man_Kg.index.isin(DF_Man_Kg.index)]

In [24]:
outliers_Man = pd.concat([outlier_Man_St,outlier_Man_Mt,outlier_Man_Se,outlier_Man_Ro,outlier_Man_Bl,outlier_Man_Ei,outlier_Man_Pa,outlier_Man_VE,outlier_Man_Kg])
outliers_Man.count()

SKU                  11846
WAREHOUSE_SECTION    11846
ORIGIN               11846
ORDER_NUMBER         11846
ORDER_POSITION       11846
PICK_VOLUME          11846
QUANTITY_UNIT        11846
DATE_TIME            11846
dtype: int64

In [25]:
print ('Range for Man - St min: ', DF_Man_St['PICK_VOLUME'].min(), ' , St max: ', DF_Man_St['PICK_VOLUME'].max())
print ('Range for Man - Mt min: ', DF_Man_Mt['PICK_VOLUME'].min(), ' , Mt max: ', DF_Man_Mt['PICK_VOLUME'].max())
print ('Range for Man - Se min: ', DF_Man_Se['PICK_VOLUME'].min(), ' , Se max: ', DF_Man_Se['PICK_VOLUME'].max())
print ('Range for Man - Ro min: ', DF_Man_Ro['PICK_VOLUME'].min(), ' , Ro max: ', DF_Man_Ro['PICK_VOLUME'].max())
print ('Range for Man - Bl min: ', DF_Man_Bl['PICK_VOLUME'].min(), ' , Bl max: ', DF_Man_Bl['PICK_VOLUME'].max())
print ('Range for Man - Ei min: ', DF_Man_Ei['PICK_VOLUME'].min(), ' , Ei max: ', DF_Man_Ei['PICK_VOLUME'].max())
print ('Range for Man - Pa min: ', DF_Man_Pa['PICK_VOLUME'].min(), ' , Pa max: ', DF_Man_Pa['PICK_VOLUME'].max())
print ('Range for Man - VE min: ', DF_Man_VE['PICK_VOLUME'].min(), ' , VE max: ', DF_Man_VE['PICK_VOLUME'].max())
print ('Range for Man - Kg min: ', DF_Man_Kg['PICK_VOLUME'].min(), ' , Kg max: ', DF_Man_Kg['PICK_VOLUME'].max())

Range for Man - St min:  1  , St max:  1186
Range for Man - Mt min:  1  , Mt max:  630
Range for Man - Se min:  1  , Se max:  4
Range for Man - Ro min:  nan  , Ro max:  nan
Range for Man - Bl min:  nan  , Bl max:  nan
Range for Man - Ei min:  nan  , Ei max:  nan
Range for Man - Pa min:  1  , Pa max:  3
Range for Man - VE min:  1  , VE max:  6
Range for Man - Kg min:  nan  , Kg max:  nan


### Kable Wahoure

In [26]:
# Cable
Pick_Kab_St = Pick_Kab.loc[(Pick_Kab.QUANTITY_UNIT == 'St')]
Pick_Kab_Mt = Pick_Kab.loc[(Pick_Kab.QUANTITY_UNIT == 'Mt')]
Pick_Kab_Se = Pick_Kab.loc[(Pick_Kab.QUANTITY_UNIT == 'Se')]
Pick_Kab_Ro = Pick_Kab.loc[(Pick_Kab.QUANTITY_UNIT == 'Ro')]
Pick_Kab_Bl = Pick_Kab.loc[(Pick_Kab.QUANTITY_UNIT == 'Bl')]
Pick_Kab_Ei = Pick_Kab.loc[(Pick_Kab.QUANTITY_UNIT == 'Ei')]
Pick_Kab_Pa = Pick_Kab.loc[(Pick_Kab.QUANTITY_UNIT == 'Pa')]
Pick_Kab_VE = Pick_Kab.loc[(Pick_Kab.QUANTITY_UNIT == 'VE')]
Pick_Kab_Kg = Pick_Kab.loc[(Pick_Kab.QUANTITY_UNIT == 'kg')]

# Non-outliers
DF_Kab_St = Pick_Kab_St[np.abs(Pick_Kab_St.PICK_VOLUME-Pick_Kab_St.PICK_VOLUME.mean()) <= (4*Pick_Kab_St.PICK_VOLUME.std())]
DF_Kab_Mt = Pick_Kab_Mt[np.abs(Pick_Kab_Mt.PICK_VOLUME-Pick_Kab_Mt.PICK_VOLUME.mean()) <= (4*Pick_Kab_Mt.PICK_VOLUME.std())]
DF_Kab_Se = Pick_Kab_Se[np.abs(Pick_Kab_Se.PICK_VOLUME-Pick_Kab_Se.PICK_VOLUME.mean()) <= (4*Pick_Kab_Se.PICK_VOLUME.std())]
DF_Kab_Ro = Pick_Kab_Ro[np.abs(Pick_Kab_Ro.PICK_VOLUME-Pick_Kab_Ro.PICK_VOLUME.mean()) <= (4*Pick_Kab_Ro.PICK_VOLUME.std())]
DF_Kab_Bl = Pick_Kab_Bl[np.abs(Pick_Kab_Bl.PICK_VOLUME-Pick_Kab_Bl.PICK_VOLUME.mean()) <= (4*Pick_Kab_Bl.PICK_VOLUME.std())]
DF_Kab_Ei = Pick_Kab_Ei[np.abs(Pick_Kab_Ei.PICK_VOLUME-Pick_Kab_Ei.PICK_VOLUME.mean()) <= (4*Pick_Kab_Ei.PICK_VOLUME.std())]
DF_Kab_Pa = Pick_Kab_Pa[np.abs(Pick_Kab_Pa.PICK_VOLUME-Pick_Kab_Pa.PICK_VOLUME.mean()) <= (4*Pick_Kab_Pa.PICK_VOLUME.std())]
DF_Kab_VE = Pick_Kab_VE[np.abs(Pick_Kab_VE.PICK_VOLUME-Pick_Kab_VE.PICK_VOLUME.mean()) <= (4*Pick_Kab_VE.PICK_VOLUME.std())]
DF_Kab_Kg = Pick_Kab_Kg[np.abs(Pick_Kab_Kg.PICK_VOLUME-Pick_Kab_Kg.PICK_VOLUME.mean()) <= (4*Pick_Kab_Kg.PICK_VOLUME.std())]

# Outliers
outlier_Kab_St = Pick_Kab_St[~Pick_Kab_St.index.isin(DF_Kab_St.index)]
outlier_Kab_Mt = Pick_Kab_Mt[~Pick_Kab_Mt.index.isin(DF_Kab_Mt.index)]
outlier_Kab_Se = Pick_Kab_Se[~Pick_Kab_Se.index.isin(DF_Kab_Se.index)]
outlier_Kab_Ro = Pick_Kab_Ro[~Pick_Kab_Ro.index.isin(DF_Kab_Ro.index)]
outlier_Kab_Bl = Pick_Kab_Bl[~Pick_Kab_Bl.index.isin(DF_Kab_Bl.index)]
outlier_Kab_Ei = Pick_Kab_Ei[~Pick_Kab_Ei.index.isin(DF_Kab_Ei.index)]
outlier_Kab_Pa = Pick_Kab_Pa[~Pick_Kab_Pa.index.isin(DF_Kab_Pa.index)]
outlier_Kab_VE = Pick_Kab_VE[~Pick_Kab_VE.index.isin(DF_Kab_VE.index)]
outlier_Kab_Kg = Pick_Kab_Kg[~Pick_Kab_Kg.index.isin(DF_Kab_Kg.index)]

In [27]:
outliers_Kab = pd.concat([outlier_Kab_St,outlier_Kab_Mt,outlier_Kab_Se,outlier_Kab_Ro,outlier_Kab_Bl,outlier_Kab_Ei,outlier_Kab_Pa,outlier_Kab_VE,outlier_Kab_Kg])
outliers_Kab.count()

SKU                  19389
WAREHOUSE_SECTION    19389
ORIGIN               19389
ORDER_NUMBER         19389
ORDER_POSITION       19389
PICK_VOLUME          19389
QUANTITY_UNIT        19389
DATE_TIME            19389
dtype: int64

In [28]:
print ('Range for Kab - St min: ', DF_Kab_St['PICK_VOLUME'].min(), ' , St max: ', DF_Kab_St['PICK_VOLUME'].max())
print ('Range for Kab - Mt min: ', DF_Kab_Mt['PICK_VOLUME'].min(), ' , Mt max: ', DF_Kab_Mt['PICK_VOLUME'].max())
print ('Range for Kab - Se min: ', DF_Kab_Se['PICK_VOLUME'].min(), ' , Se max: ', DF_Kab_Se['PICK_VOLUME'].max())
print ('Range for Kab - Ro min: ', DF_Kab_Ro['PICK_VOLUME'].min(), ' , Ro max: ', DF_Kab_Ro['PICK_VOLUME'].max())
print ('Range for Kab - Bl min: ', DF_Kab_Bl['PICK_VOLUME'].min(), ' , Bl max: ', DF_Kab_Bl['PICK_VOLUME'].max())
print ('Range for Kab - Ei min: ', DF_Kab_Ei['PICK_VOLUME'].min(), ' , Ei max: ', DF_Kab_Ei['PICK_VOLUME'].max())
print ('Range for Kab - Pa min: ', DF_Kab_Pa['PICK_VOLUME'].min(), ' , Pa max: ', DF_Kab_Pa['PICK_VOLUME'].max())
print ('Range for Kab - VE min: ', DF_Kab_VE['PICK_VOLUME'].min(), ' , VE max: ', DF_Kab_VE['PICK_VOLUME'].max())
print ('Range for Kab - Kg min: ', DF_Kab_Kg['PICK_VOLUME'].min(), ' , Kg max: ', DF_Kab_Kg['PICK_VOLUME'].max())

Range for Kab - St min:  1  , St max:  2600
Range for Kab - Mt min:  1  , Mt max:  2650
Range for Kab - Se min:  nan  , Se max:  nan
Range for Kab - Ro min:  nan  , Ro max:  nan
Range for Kab - Bl min:  nan  , Bl max:  nan
Range for Kab - Ei min:  nan  , Ei max:  nan
Range for Kab - Pa min:  nan  , Pa max:  nan
Range for Kab - VE min:  nan  , VE max:  nan
Range for Kab - Kg min:  nan  , Kg max:  nan


### Combining all the WH data back

In [29]:
# Creating a dataframe that does not contain outliers
pickDF_cleaned = pd.concat([DF_SHL_St,DF_SHL_Mt,DF_SHL_Se,DF_SHL_Ro,DF_SHL_Bl,DF_SHL_Ei,DF_SHL_Pa,DF_SHL_VE,DF_SHL_Kg  #SHL
                        ,DF_AKL_St,DF_AKL_Mt,DF_AKL_Se,DF_AKL_Ro,DF_AKL_Bl,DF_AKL_Ei,DF_AKL_Pa,DF_AKL_VE,DF_AKL_Kg  #AKL
                        ,DF_HRL_St,DF_HRL_Mt,DF_HRL_Se,DF_HRL_Ro,DF_HRL_Bl,DF_HRL_Ei,DF_HRL_Pa,DF_HRL_VE,DF_HRL_Kg  #HRL
                        ,DF_Man_St,DF_Man_Mt,DF_Man_Se,DF_Man_Ro,DF_Man_Bl,DF_Man_Ei,DF_Man_Pa,DF_Man_VE,DF_Man_Kg  #Manual 
                        ,DF_Kab_St,DF_Kab_Mt,DF_Kab_Se,DF_Kab_Ro,DF_Kab_Bl,DF_Kab_Ei,DF_Kab_Pa,DF_Kab_VE,DF_Kab_Kg]) #Kabel

## Result of the cleaning 

In [30]:
display(pickDF_cleaned)

SKU WAREHOUSE_SECTION  ORIGIN ORDER_NUMBER  ORDER_POSITION  \
0         000002               SHL      48     07055448               1   
1         000002               SHL      48     07055448               1   
2         000002               SHL      48     07055448               1   
3         000002               SHL      48     07055448               1   
4         000002               SHL      48     07055448               1   
...          ...               ...     ...          ...             ...   
33888980  129914        Kabellager      48     18547561               2   
33888981  189976        Kabellager      48     06108542               3   
33888982  189976        Kabellager      48     06108542               4   
33888983  189976        Kabellager      48     06108542               2   
33888984  189976        Kabellager      48     06108542               1   

          PICK_VOLUME QUANTITY_UNIT           DATE_TIME  
0                  30            St 2017-06-30 11:22:35  
1                  30            St 2017-06-30 12:04:50  
2                  20            St 2017-06-30 12:04:51  
3                  30            St 2017-06-30 12:05:02  
4                  12            St 2017-06-30 12:05:12  
...               ...           ...                 ...  
33888980            2            Mt 2016-12-30 16:21:00  
33888981           30            Mt 2016-12-30 16:29:13  
33888982           30            Mt 2016-12-30 16:29:21  
33888983           30            Mt 2016-12-30 16:29:27  
33888984           30            Mt 2016-12-30 16:29:35  

[33374104 rows x 8 columns]

# Data Cleaning - Product Data

In [31]:
query = "SELECT * FROM product_data"
productDF = pd.read_sql(query, onn)
display(productDF)

C:\Users\HayateSato\AppData\Local\Temp\ipykernel_12336\760909004.py:2: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  productDF = pd.read_sql(query, onn)


PRODUCT_ID                     DESCRIPTION  \
0           000052        PUNCH II MSW1 1500mm PUN   
1          1036628              H05VV-F2X1 5WS 50M   
2          1052053                 H07RN-F3G1 100M   
3           110109  SIEM DELTA Doppelta 2S 5TD2111   
4           110125  SIEM PLUS Wip Univ ews 5TG7581   
...            ...                             ...   
2199639     Z53390     ASJ MD300EB NH-Lasttrennlei   
2199640     Z53392     ASJ MD31B NH-Lasttrennleist   
2199641     Z53394     ASJ MD31HB NH-Lasttrennleis   
2199642     Z50507   ABB LLEG124X560MM24 LED LLEG1   
2199643     Z52127   ABB SLADCG250MM700 LED SLA DC   

                        PRODUCT_GROUP  
0                       35_Leuchten\r  
1                 16_Sonderverkäufe\r  
2                 16_Sonderverkäufe\r  
3        32_Schalter_Steckvorrichtg\r  
4        32_Schalter_Steckvorrichtg\r  
...                               ...  
2199639       34_Verteiler_Schränke\r  
2199640       34_Verteiler_Schränke\r  
2199641       34_Verteiler_Schränke\r  
2199642             37_Leuchtmittel\r  
2199643             37_Leuchtmittel\r  

[2199644 rows x 3 columns]

## Empty Cells 

In [32]:
# Checking if there is empty cells 
display(productDF.isnull().sum())
display("-------------")
# Priting out the percentage of empty cells 
display(productDF.isnull().sum()/len(productDF))

PRODUCT_ID        0
DESCRIPTION       0
PRODUCT_GROUP    71
dtype: int64

'-------------'

PRODUCT_ID       0.000000
DESCRIPTION      0.000000
PRODUCT_GROUP    0.000032
dtype: float64

In [33]:
# extracting only rows that contain empty values
missing = productDF[productDF.isnull().any(axis=1)]
display(missing)

# Filling the empty values "No Description"
productDF_filled = productDF.fillna(value="No Description")

# Checking if there is empty cells 
display(productDF_filled.isnull().sum())
print("----------------")
# Checking if there is empty cells in percentage
display(productDF_filled.isnull().sum()/len(productDF_filled))
print("----------------")
display(f"the number of rows: {len(productDF_filled)}")

### use productDF_filled from here after

PRODUCT_ID                 DESCRIPTION PRODUCT_GROUP
133757      A99331  PSE Spachtel,19_Werkzeug\r          None
746492      J10131         LAURA,35_Leuchten\r          None
746493      J10133         LAURA,35_Leuchten\r          None
751738      J10127         LAURA,35_Leuchten\r          None
752400      J10125         LAURA,35_Leuchten\r          None
...            ...                         ...           ...
2050050     Z09432         FENDA,35_Leuchten\r          None
2050051     Z09436         FENDA,35_Leuchten\r          None
2050143     Z09445         FENDA,35_Leuchten\r          None
2050144     Z09463         FENDA,35_Leuchten\r          None
2117088     Z96456            SLC,41_Antenne\r          None

[71 rows x 3 columns]

PRODUCT_ID       0
DESCRIPTION      0
PRODUCT_GROUP    0
dtype: int64

----------------


PRODUCT_ID       0.0
DESCRIPTION      0.0
PRODUCT_GROUP    0.0
dtype: float64

----------------


'the number of rows: 2199644'

## Special characters

In [34]:
# counting how many rows that contain umlaut in "description column"
ae_des = productDF_filled[productDF_filled["DESCRIPTION"].str.contains("ä", case=False)]
oe_des = productDF_filled[productDF_filled["DESCRIPTION"].str.contains("ü", case=False)]
ue_des = productDF_filled[productDF_filled["DESCRIPTION"].str.contains("ö", case=False)]
ss_des = productDF_filled[productDF_filled["DESCRIPTION"].str.contains("ß", case=False)]


# counting how many rows that contain umlaut in "product_group column" 
ae_pg = productDF_filled[productDF_filled["PRODUCT_GROUP"].str.contains("ä", case=False)]
oe_pg = productDF_filled[productDF_filled["PRODUCT_GROUP"].str.contains("ü", case=False)]
ue_pg = productDF_filled[productDF_filled["PRODUCT_GROUP"].str.contains("ö", case=False)]
ss_pg = productDF_filled[productDF_filled["PRODUCT_GROUP"].str.contains("ß", case=False)]

In [35]:
# pd.options.display.float_format = '{:,.0f}'.format
print(f"DESCRIPTION \n Ä : {len(ae_des)} rows, of which % : {len(ae_des)/len(productDF_filled)} \n Ö : {len(oe_des)} rows, of which % : {len(oe_des)/len(productDF_filled)}  \n Ü : {len(ue_des)} rows, of which % : {len(ue_des)/len(productDF_filled)}  \n ß : {len(ss_des)} rows, of which % : {len(ss_des)/len(productDF_filled)} ")
print("-------------------")
print(f"PRODUCT_GROUP \n Ä : {len(ae_pg)} rows, of which % : {len(ae_pg)/len(productDF_filled)} \n Ö : {len(oe_pg)} rows, of which % : {len(oe_pg)/len(productDF_filled)}  \n Ü : {len(ue_pg)} rows, of which % : {len(ue_pg)/len(productDF_filled)}  \n ß : {len(ss_pg)} rows, of which % : {len(ss_pg)/len(productDF_filled)} ")


DESCRIPTION 
 Ä : 88115 rows, of which % : 0.040058754962166605 
 Ö : 153219 rows, of which % : 0.06965627165123084  
 Ü : 26258 rows, of which % : 0.011937386231590203  
 ß : 37917 rows, of which % : 0.01723778938773729 
-------------------
PRODUCT_GROUP 
 Ä : 791242 rows, of which % : 0.3597136627563369 
 Ö : 78178 rows, of which % : 0.035541205758750055  
 Ü : 0 rows, of which % : 0.0  
 ß : 0 rows, of which % : 0.0 


In [36]:
# checking the percentage
display(len(ae_des)/len(productDF_filled))
display(len(oe_des)/len(productDF_filled))
display(len(ue_des)/len(productDF_filled))
display(len(ss_des)/len(productDF_filled))
# display(len(ae_des)/len(productDF_filled))

0.040058754962166605

0.06965627165123084

0.011937386231590203

0.01723778938773729

In [37]:
productDF_filled["DESCRIPTION"].value_counts()

DESCRIPTION
Klemmenmarkierung                      11251
Phoe Leiterplattensteckverb             6267
                                        6023
Siem Leistungsschalter 3VA1             5849
Siem Leistungsschalter 3VA2             5520
                                       ...  
AA 6IEAV173100/9001 Inneneck ST 173        1
AA KS9RWEKE S99-Kreuzschalt                1
AA KS9CWEKE S99-Kreuzschalt                1
AA SK61UT3/98 Sägekern 61UT3/              1
ABB LLEG124X560MM24 LED LLEG1              1
Name: count, Length: 1422864, dtype: int64

In [38]:
# creating a list of special letters in lower case that needs to be replaced
umlaut_mapping_low = {'ä': 'ae', 'ö': 'oe', 'ü': 'ue', 'ß': 'ss'}

In [39]:
# creating a list of special letters in UPPER case that needs to be replaced
umlaut_mapping_up = {}

umlaut_mapping_up = {k.upper():v.upper() for k,v in umlaut_mapping_low.items()}
umlaut_mapping_up

{'Ä': 'AE', 'Ö': 'OE', 'Ü': 'UE', 'SS': 'SS'}

In [40]:
# combining the two lists 
umlaut_mapping = umlaut_mapping_low.copy() 

for key, value in umlaut_mapping_up.items():
    umlaut_mapping[key] = value

umlaut_mapping

{'ä': 'ae',
 'ö': 'oe',
 'ü': 'ue',
 'ß': 'ss',
 'Ä': 'AE',
 'Ö': 'OE',
 'Ü': 'UE',
 'SS': 'SS'}

In [41]:
# replacing the special letters and naming the dataframe "productDF_cleaned
productDF_cleaned = productDF_filled.copy()
productDF_cleaned["DESCRIPTION"] = productDF_cleaned["DESCRIPTION"].replace(umlaut_mapping, regex=True)
productDF_cleaned["PRODUCT_GROUP"] = productDF_cleaned["PRODUCT_GROUP"].replace(umlaut_mapping, regex=True)

In [42]:
# checking the result
productDF_cleaned[productDF_cleaned["DESCRIPTION"].str.contains("ä", case=False)]

Empty DataFrame
Columns: [PRODUCT_ID, DESCRIPTION, PRODUCT_GROUP]
Index: []

In [43]:
# checking the result
productDF_cleaned[productDF_cleaned["PRODUCT_GROUP"].str.contains("ä", case=False)]

Empty DataFrame
Columns: [PRODUCT_ID, DESCRIPTION, PRODUCT_GROUP]
Index: []

In [44]:
# checking the result
ae_des_C = productDF_cleaned[productDF_cleaned["DESCRIPTION"].str.contains("ä", case=False)]
oe_des_C = productDF_cleaned[productDF_cleaned["DESCRIPTION"].str.contains("ü", case=False)]
ue_des_C = productDF_cleaned[productDF_cleaned["DESCRIPTION"].str.contains("ö", case=False)]
ss_des_C = productDF_cleaned[productDF_cleaned["DESCRIPTION"].str.contains("ß", case=False)]

ae_pg_C = productDF_cleaned[productDF_cleaned["PRODUCT_GROUP"].str.contains("ä", case=False)]
oe_pg_C = productDF_cleaned[productDF_cleaned["PRODUCT_GROUP"].str.contains("ü", case=False)]
ue_pg_C = productDF_cleaned[productDF_cleaned["PRODUCT_GROUP"].str.contains("ö", case=False)]
ss_pg_C = productDF_cleaned[productDF_cleaned["PRODUCT_GROUP"].str.contains("ß", case=False)]

print(f"DESCRIPTION \n Ä : {len(ae_des_C)} rows \n Ö : {len(oe_des_C)} rows \n Ü : {len(ue_des_C)} rows \n ß : {len(ss_des_C)} rows")
print("-------------------")
print(f"PRODUCT_GROUP \n Ä : {len(ae_pg_C)} rows \n Ö : {len(oe_pg_C)} rows \n Ü : {len(ue_pg_C)} rows \n ß : {len(ss_pg_C)} rows")

DESCRIPTION 
 Ä : 0 rows 
 Ö : 0 rows 
 Ü : 0 rows 
 ß : 0 rows
-------------------
PRODUCT_GROUP 
 Ä : 0 rows 
 Ö : 0 rows 
 Ü : 0 rows 
 ß : 0 rows


# Data Cleaning - Warehouse Section

In [45]:
query = "SELECT * FROM warehouse_section"
WH_df = pd.read_sql(query, onn)
display(WH_df)

C:\Users\HayateSato\AppData\Local\Temp\ipykernel_12336\230299934.py:2: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  WH_df = pd.read_sql(query, onn)


ABREVIATION                          WH_NAME     WH_GROUP  \
0          AKL   Automatisches-Kleinteile-Lager          AKL   
1          HOF                        Hof-Lager   Kabellager   
2          HRL    Hoch-Regal-Lager für Paletten          HRL   
3          LGL                    Langgut-Lager      Manuell   
4          MHL         Außenlager bei Spedition      Obsolet   
5          MKL    Manuelles-Kommissionier-Lager      Manuell   
6          MNL        Manuelles-Nachschub-Lager      Manuell   
7          SGL                Schnell-Gut-Lager      Obsolet   
8          SHL                    Shuttle-Lager          SHL   
9          SKL      Schnellläuferzone-AKL-Kommi      Obsolet   
10         SNL  Schnellläuferzone-AKL-Nachschub      Obsolet   
11         SPL  Schnellläuferzone-Palettenlager      Obsolet   
12         TRA               Trommel-Außenlager   Kabellager   
13         TRB               Trommel-Blocklager   Kabellager   
14         TRK                    Trommel-Lager   Kabellager   
15         TRN            Trommel-Reserve-Lager   Kabellager   
16         TRR             Trommel Reste im TRK   Kabellager   
17         VTO                      Verladetore  Verladetore   

    DATA_AVAILABILITY  
0                 AKL  
1          Kabellager  
2                 HRL  
3             Manuell  
4   (nicht vorhanden)  
5             Manuell  
6             Manuell  
7   (nicht vorhanden)  
8                 SHL  
9   (nicht vorhanden)  
10  (nicht vorhanden)  
11  (nicht vorhanden)  
12         Kabellager  
13         Kabellager  
14         Kabellager  
15         Kabellager  
16         Kabellager  
17  (nicht vorhanden)

## Handling special letters

In [46]:
WH_CleanLetter = WH_df.copy()
WH_CleanLetter["WH_NAME"] = WH_CleanLetter["WH_NAME"].replace(umlaut_mapping, regex=True)
WH_CleanLetter

ABREVIATION                           WH_NAME     WH_GROUP  \
0          AKL    Automatisches-Kleinteile-Lager          AKL   
1          HOF                         Hof-Lager   Kabellager   
2          HRL    Hoch-Regal-Lager fuer Paletten          HRL   
3          LGL                     Langgut-Lager      Manuell   
4          MHL         Aussenlager bei Spedition      Obsolet   
5          MKL     Manuelles-Kommissionier-Lager      Manuell   
6          MNL         Manuelles-Nachschub-Lager      Manuell   
7          SGL                 Schnell-Gut-Lager      Obsolet   
8          SHL                     Shuttle-Lager          SHL   
9          SKL      Schnelllaeuferzone-AKL-Kommi      Obsolet   
10         SNL  Schnelllaeuferzone-AKL-Nachschub      Obsolet   
11         SPL  Schnelllaeuferzone-Palettenlager      Obsolet   
12         TRA               Trommel-Aussenlager   Kabellager   
13         TRB                Trommel-Blocklager   Kabellager   
14         TRK                     Trommel-Lager   Kabellager   
15         TRN             Trommel-Reserve-Lager   Kabellager   
16         TRR              Trommel Reste im TRK   Kabellager   
17         VTO                       Verladetore  Verladetore   

    DATA_AVAILABILITY  
0                 AKL  
1          Kabellager  
2                 HRL  
3             Manuell  
4   (nicht vorhanden)  
5             Manuell  
6             Manuell  
7   (nicht vorhanden)  
8                 SHL  
9   (nicht vorhanden)  
10  (nicht vorhanden)  
11  (nicht vorhanden)  
12         Kabellager  
13         Kabellager  
14         Kabellager  
15         Kabellager  
16         Kabellager  
17  (nicht vorhanden)

## Unused Warehouse Sections

In [47]:
# Deleting the warehouse sections that have no data registered 
WH_InUse = WH_CleanLetter[(WH_CleanLetter["WH_GROUP"] != "Obsolet") & (WH_CleanLetter["WH_GROUP"] != "Verladetore")]
### WH_InUse = WH_CleanLetter[WH_CleanLetter["DATA_AVAILABILITY"] != "(nicht vorhanden)"]  # simpler but same result 

WH_InUse

ABREVIATION                         WH_NAME    WH_GROUP DATA_AVAILABILITY
0          AKL  Automatisches-Kleinteile-Lager         AKL               AKL
1          HOF                       Hof-Lager  Kabellager        Kabellager
2          HRL  Hoch-Regal-Lager fuer Paletten         HRL               HRL
3          LGL                   Langgut-Lager     Manuell           Manuell
5          MKL   Manuelles-Kommissionier-Lager     Manuell           Manuell
6          MNL       Manuelles-Nachschub-Lager     Manuell           Manuell
8          SHL                   Shuttle-Lager         SHL               SHL
12         TRA             Trommel-Aussenlager  Kabellager        Kabellager
13         TRB              Trommel-Blocklager  Kabellager        Kabellager
14         TRK                   Trommel-Lager  Kabellager        Kabellager
15         TRN           Trommel-Reserve-Lager  Kabellager        Kabellager
16         TRR            Trommel Reste im TRK  Kabellager        Kabellager

## Deleting DATA_AVAILABILITY Column

In [48]:
WH_Cleaned = WH_InUse.drop(columns=["DATA_AVAILABILITY"])

WH_Cleaned
### we can use this as data table for warehouse 

ABREVIATION                         WH_NAME    WH_GROUP
0          AKL  Automatisches-Kleinteile-Lager         AKL
1          HOF                       Hof-Lager  Kabellager
2          HRL  Hoch-Regal-Lager fuer Paletten         HRL
3          LGL                   Langgut-Lager     Manuell
5          MKL   Manuelles-Kommissionier-Lager     Manuell
6          MNL       Manuelles-Nachschub-Lager     Manuell
8          SHL                   Shuttle-Lager         SHL
12         TRA             Trommel-Aussenlager  Kabellager
13         TRB              Trommel-Blocklager  Kabellager
14         TRK                   Trommel-Lager  Kabellager
15         TRN           Trommel-Reserve-Lager  Kabellager
16         TRR            Trommel Reste im TRK  Kabellager

# Preparing Tables according to ER model

## Creating "YEAR", "MONTH", "QUARTER" column

In [49]:
pickDF_cleaned.dtypes

SKU                          object
WAREHOUSE_SECTION            object
ORIGIN                        int64
ORDER_NUMBER                 object
ORDER_POSITION                int64
PICK_VOLUME                   int64
QUANTITY_UNIT                object
DATE_TIME            datetime64[ns]
dtype: object

In [50]:
pickDF_cleaned['DATE_TIME'] = pd.to_datetime(pickDF_cleaned['DATE_TIME'])   #convert col to date-time datatype
pickDF_cleaned['YEAR'] = pickDF_cleaned['DATE_TIME'].dt.year 
pickDF_cleaned['MONTH'] = pickDF_cleaned['DATE_TIME'].dt.month
pickDF_cleaned['QUARTER'] = np.ceil(pickDF_cleaned['MONTH'] / 3).astype(int)
pickDF_cleaned['TIME'] = pickDF_cleaned['DATE_TIME'].dt.time
pickDF_cleaned.head()

SKU WAREHOUSE_SECTION  ORIGIN ORDER_NUMBER  ORDER_POSITION  PICK_VOLUME  \
0  000002               SHL      48     07055448               1           30   
1  000002               SHL      48     07055448               1           30   
2  000002               SHL      48     07055448               1           20   
3  000002               SHL      48     07055448               1           30   
4  000002               SHL      48     07055448               1           12   

  QUANTITY_UNIT           DATE_TIME  YEAR  MONTH  QUARTER      TIME  
0            St 2017-06-30 11:22:35  2017      6        2  11:22:35  
1            St 2017-06-30 12:04:50  2017      6        2  12:04:50  
2            St 2017-06-30 12:04:51  2017      6        2  12:04:51  
3            St 2017-06-30 12:05:02  2017      6        2  12:05:02  
4            St 2017-06-30 12:05:12  2017      6        2  12:05:12

## Creating Unique Order Number

In [51]:
### Currently, order number contains recurring number so we need to assign unique order number
### by combining "Year" and "ORDER_NUMBER", we will make unique order number

# Checking the data type
pickDF_cleaned.dtypes

SKU                          object
WAREHOUSE_SECTION            object
ORIGIN                        int64
ORDER_NUMBER                 object
ORDER_POSITION                int64
PICK_VOLUME                   int64
QUANTITY_UNIT                object
DATE_TIME            datetime64[ns]
YEAR                          int32
MONTH                         int32
QUARTER                       int32
TIME                         object
dtype: object

In [52]:
pickDF_cleaned["UNIQUE_ORDER_NUMBER"] = pickDF_cleaned["YEAR"].astype(str) + "-" + pickDF_cleaned["ORDER_NUMBER"].astype(str)
pickDF_cleaned

SKU WAREHOUSE_SECTION  ORIGIN ORDER_NUMBER  ORDER_POSITION  \
0         000002               SHL      48     07055448               1   
1         000002               SHL      48     07055448               1   
2         000002               SHL      48     07055448               1   
3         000002               SHL      48     07055448               1   
4         000002               SHL      48     07055448               1   
...          ...               ...     ...          ...             ...   
33888980  129914        Kabellager      48     18547561               2   
33888981  189976        Kabellager      48     06108542               3   
33888982  189976        Kabellager      48     06108542               4   
33888983  189976        Kabellager      48     06108542               2   
33888984  189976        Kabellager      48     06108542               1   

          PICK_VOLUME QUANTITY_UNIT           DATE_TIME  YEAR  MONTH  QUARTER  \
0                  30            St 2017-06-30 11:22:35  2017      6        2   
1                  30            St 2017-06-30 12:04:50  2017      6        2   
2                  20            St 2017-06-30 12:04:51  2017      6        2   
3                  30            St 2017-06-30 12:05:02  2017      6        2   
4                  12            St 2017-06-30 12:05:12  2017      6        2   
...               ...           ...                 ...   ...    ...      ...   
33888980            2            Mt 2016-12-30 16:21:00  2016     12        4   
33888981           30            Mt 2016-12-30 16:29:13  2016     12        4   
33888982           30            Mt 2016-12-30 16:29:21  2016     12        4   
33888983           30            Mt 2016-12-30 16:29:27  2016     12        4   
33888984           30            Mt 2016-12-30 16:29:35  2016     12        4   

              TIME UNIQUE_ORDER_NUMBER  
0         11:22:35       2017-07055448  
1         12:04:50       2017-07055448  
2         12:04:51       2017-07055448  
3         12:05:02       2017-07055448  
4         12:05:12       2017-07055448  
...            ...                 ...  
33888980  16:21:00       2016-18547561  
33888981  16:29:13       2016-06108542  
33888982  16:29:21       2016-06108542  
33888983  16:29:27       2016-06108542  
33888984  16:29:35       2016-06108542  

[33374104 rows x 13 columns]

# Separating Data Table

## Standalone Table

In [53]:
Standalone_Table = pd.DataFrame(pickDF_cleaned[["UNIQUE_ORDER_NUMBER", "ORDER_POSITION"]])
Standalone_Table

UNIQUE_ORDER_NUMBER  ORDER_POSITION
0              2017-07055448               1
1              2017-07055448               1
2              2017-07055448               1
3              2017-07055448               1
4              2017-07055448               1
...                      ...             ...
33888980       2016-18547561               2
33888981       2016-06108542               3
33888982       2016-06108542               4
33888983       2016-06108542               2
33888984       2016-06108542               1

[33374104 rows x 2 columns]

## Origin Table

In [54]:
###### NOT IN USE #######

# Origin_Table = pickDF_cleaned[["UNIQUE_ORDER_NUMBER", "ORIGIN"]]
# Origin_Table

## Product Table

In [55]:
product_table = productDF_cleaned.copy()
product_table 

PRODUCT_ID                     DESCRIPTION  \
0           000052        PUNCH II MSW1 1500mm PUN   
1          1036628              H05VV-F2X1 5WS 50M   
2          1052053                 H07RN-F3G1 100M   
3           110109  SIEM DELTA Doppelta 2S 5TD2111   
4           110125  SIEM PLUS Wip Univ ews 5TG7581   
...            ...                             ...   
2199639     Z53390     ASJ MD300EB NH-Lasttrennlei   
2199640     Z53392     ASJ MD31B NH-Lasttrennleist   
2199641     Z53394     ASJ MD31HB NH-Lasttrennleis   
2199642     Z50507   ABB LLEG124X560MM24 LED LLEG1   
2199643     Z52127   ABB SLADCG250MM700 LED SLA DC   

                        PRODUCT_GROUP  
0                       35_Leuchten\r  
1                16_Sonderverkaeufe\r  
2                16_Sonderverkaeufe\r  
3        32_Schalter_Steckvorrichtg\r  
4        32_Schalter_Steckvorrichtg\r  
...                               ...  
2199639      34_Verteiler_Schraenke\r  
2199640      34_Verteiler_Schraenke\r  
2199641      34_Verteiler_Schraenke\r  
2199642             37_Leuchtmittel\r  
2199643             37_Leuchtmittel\r  

[2199644 rows x 3 columns]

## Date Table

In [56]:
Date_only = pickDF_cleaned[["UNIQUE_ORDER_NUMBER", "YEAR", "QUARTER", "MONTH", "TIME", "DATE_TIME"]]
Date_only 

UNIQUE_ORDER_NUMBER  YEAR  QUARTER  MONTH      TIME  \
0              2017-07055448  2017        2      6  11:22:35   
1              2017-07055448  2017        2      6  12:04:50   
2              2017-07055448  2017        2      6  12:04:51   
3              2017-07055448  2017        2      6  12:05:02   
4              2017-07055448  2017        2      6  12:05:12   
...                      ...   ...      ...    ...       ...   
33888980       2016-18547561  2016        4     12  16:21:00   
33888981       2016-06108542  2016        4     12  16:29:13   
33888982       2016-06108542  2016        4     12  16:29:21   
33888983       2016-06108542  2016        4     12  16:29:27   
33888984       2016-06108542  2016        4     12  16:29:35   

                   DATE_TIME  
0        2017-06-30 11:22:35  
1        2017-06-30 12:04:50  
2        2017-06-30 12:04:51  
3        2017-06-30 12:05:02  
4        2017-06-30 12:05:12  
...                      ...  
33888980 2016-12-30 16:21:00  
33888981 2016-12-30 16:29:13  
33888982 2016-12-30 16:29:21  
33888983 2016-12-30 16:29:27  
33888984 2016-12-30 16:29:35  

[33374104 rows x 6 columns]

In [57]:
Date_copy = Date_only.copy()

# Converting into datatime format and making a new column for date value "YYYY-MM-DD HH:MM:SS"
Date_copy["DATE_TIME"] = pd.to_datetime(Date_copy["DATE_TIME"])
Date_copy["DATE"] = Date_copy["DATE_TIME"].dt.date

# Converting into datatime format and making a new column for day of day of month 
Date_copy["DATE"] = pd.to_datetime(Date_copy["DATE"])
Date_copy['DAY_OF_MONTH'] = Date_copy['DATE'].dt.day

# Converting into datatime format and making a new column for day of week 
Date_copy["DATE"] = pd.to_datetime(Date_copy["DATE"])
Date_copy['DAY_OF_WEEK'] = Date_copy['DATE'].dt.day_name()


# I have re-structure annd make the "DATE_TIME" column as the primal key
Date_copy

UNIQUE_ORDER_NUMBER  YEAR  QUARTER  MONTH      TIME  \
0              2017-07055448  2017        2      6  11:22:35   
1              2017-07055448  2017        2      6  12:04:50   
2              2017-07055448  2017        2      6  12:04:51   
3              2017-07055448  2017        2      6  12:05:02   
4              2017-07055448  2017        2      6  12:05:12   
...                      ...   ...      ...    ...       ...   
33888980       2016-18547561  2016        4     12  16:21:00   
33888981       2016-06108542  2016        4     12  16:29:13   
33888982       2016-06108542  2016        4     12  16:29:21   
33888983       2016-06108542  2016        4     12  16:29:27   
33888984       2016-06108542  2016        4     12  16:29:35   

                   DATE_TIME       DATE  DAY_OF_MONTH DAY_OF_WEEK  
0        2017-06-30 11:22:35 2017-06-30            30      Friday  
1        2017-06-30 12:04:50 2017-06-30            30      Friday  
2        2017-06-30 12:04:51 2017-06-30            30      Friday  
3        2017-06-30 12:05:02 2017-06-30            30      Friday  
4        2017-06-30 12:05:12 2017-06-30            30      Friday  
...                      ...        ...           ...         ...  
33888980 2016-12-30 16:21:00 2016-12-30            30      Friday  
33888981 2016-12-30 16:29:13 2016-12-30            30      Friday  
33888982 2016-12-30 16:29:21 2016-12-30            30      Friday  
33888983 2016-12-30 16:29:27 2016-12-30            30      Friday  
33888984 2016-12-30 16:29:35 2016-12-30            30      Friday  

[33374104 rows x 9 columns]

In [58]:
# re-ordering the order of columns
Date_cleaned = Date_copy[["UNIQUE_ORDER_NUMBER", "DATE_TIME", "YEAR", "QUARTER", "MONTH", "DAY_OF_WEEK", "DAY_OF_MONTH", "TIME"]]
Date_cleaned

UNIQUE_ORDER_NUMBER           DATE_TIME  YEAR  QUARTER  MONTH  \
0              2017-07055448 2017-06-30 11:22:35  2017        2      6   
1              2017-07055448 2017-06-30 12:04:50  2017        2      6   
2              2017-07055448 2017-06-30 12:04:51  2017        2      6   
3              2017-07055448 2017-06-30 12:05:02  2017        2      6   
4              2017-07055448 2017-06-30 12:05:12  2017        2      6   
...                      ...                 ...   ...      ...    ...   
33888980       2016-18547561 2016-12-30 16:21:00  2016        4     12   
33888981       2016-06108542 2016-12-30 16:29:13  2016        4     12   
33888982       2016-06108542 2016-12-30 16:29:21  2016        4     12   
33888983       2016-06108542 2016-12-30 16:29:27  2016        4     12   
33888984       2016-06108542 2016-12-30 16:29:35  2016        4     12   

         DAY_OF_WEEK  DAY_OF_MONTH      TIME  
0             Friday            30  11:22:35  
1             Friday            30  12:04:50  
2             Friday            30  12:04:51  
3             Friday            30  12:05:02  
4             Friday            30  12:05:12  
...              ...           ...       ...  
33888980      Friday            30  16:21:00  
33888981      Friday            30  16:29:13  
33888982      Friday            30  16:29:21  
33888983      Friday            30  16:29:27  
33888984      Friday            30  16:29:35  

[33374104 rows x 8 columns]

#### Order duratoin

In [59]:
Ord_dur = Date_cleaned.groupby(['UNIQUE_ORDER_NUMBER'])['TIME'].agg(['min', 'max']).reset_index()
Ord_dur

UNIQUE_ORDER_NUMBER       min       max
0             2011-02000001  08:29:17  08:29:17
1             2011-02000003  10:16:06  10:20:56
2             2011-02000006  12:43:16  12:43:58
3             2011-02000011  00:26:35  00:27:37
4             2011-02000014  12:58:56  13:04:29
...                     ...       ...       ...
9342945       2020-99881951  11:18:30  11:18:30
9342946       2020-99882431  10:00:51  10:00:51
9342947       2020-99882521  13:02:38  13:02:38
9342948       2020-99883962  13:36:49  13:38:01
9342949       2020-99884033  14:10:56  14:10:56

[9342950 rows x 3 columns]

In [60]:
Ord_duration = Ord_dur.copy()

In [61]:
# Adding sample date '1900-01-01 ' to avoid conversion errors. This avoids run errors, and also does not affect the outcome
Ord_duration['min'] = pd.to_datetime('1900-01-01 ' + Ord_duration['min'].astype(str))
Ord_duration['max'] = pd.to_datetime('1900-01-01 ' + Ord_duration['max'].astype(str))
Ord_duration

UNIQUE_ORDER_NUMBER                 min                 max
0             2011-02000001 1900-01-01 08:29:17 1900-01-01 08:29:17
1             2011-02000003 1900-01-01 10:16:06 1900-01-01 10:20:56
2             2011-02000006 1900-01-01 12:43:16 1900-01-01 12:43:58
3             2011-02000011 1900-01-01 00:26:35 1900-01-01 00:27:37
4             2011-02000014 1900-01-01 12:58:56 1900-01-01 13:04:29
...                     ...                 ...                 ...
9342945       2020-99881951 1900-01-01 11:18:30 1900-01-01 11:18:30
9342946       2020-99882431 1900-01-01 10:00:51 1900-01-01 10:00:51
9342947       2020-99882521 1900-01-01 13:02:38 1900-01-01 13:02:38
9342948       2020-99883962 1900-01-01 13:36:49 1900-01-01 13:38:01
9342949       2020-99884033 1900-01-01 14:10:56 1900-01-01 14:10:56

[9342950 rows x 3 columns]

In [62]:
Ord_duration['DURATION_MINUTES'] = (Ord_duration['max'] - Ord_duration['min']).dt.total_seconds() / 60
Ord_duration

UNIQUE_ORDER_NUMBER                 min                 max  \
0             2011-02000001 1900-01-01 08:29:17 1900-01-01 08:29:17   
1             2011-02000003 1900-01-01 10:16:06 1900-01-01 10:20:56   
2             2011-02000006 1900-01-01 12:43:16 1900-01-01 12:43:58   
3             2011-02000011 1900-01-01 00:26:35 1900-01-01 00:27:37   
4             2011-02000014 1900-01-01 12:58:56 1900-01-01 13:04:29   
...                     ...                 ...                 ...   
9342945       2020-99881951 1900-01-01 11:18:30 1900-01-01 11:18:30   
9342946       2020-99882431 1900-01-01 10:00:51 1900-01-01 10:00:51   
9342947       2020-99882521 1900-01-01 13:02:38 1900-01-01 13:02:38   
9342948       2020-99883962 1900-01-01 13:36:49 1900-01-01 13:38:01   
9342949       2020-99884033 1900-01-01 14:10:56 1900-01-01 14:10:56   

         DURATION_MINUTES  
0                0.000000  
1                4.833333  
2                0.700000  
3                1.033333  
4                5.550000  
...                   ...  
9342945          0.000000  
9342946          0.000000  
9342947          0.000000  
9342948          1.200000  
9342949          0.000000  

[9342950 rows x 4 columns]

In [63]:
# Deleting unnecessary columns 
Duration_Minutes = Ord_duration.drop(columns=['min', 'max'])
Duration_Minutes

UNIQUE_ORDER_NUMBER  DURATION_MINUTES
0             2011-02000001          0.000000
1             2011-02000003          4.833333
2             2011-02000006          0.700000
3             2011-02000011          1.033333
4             2011-02000014          5.550000
...                     ...               ...
9342945       2020-99881951          0.000000
9342946       2020-99882431          0.000000
9342947       2020-99882521          0.000000
9342948       2020-99883962          1.200000
9342949       2020-99884033          0.000000

[9342950 rows x 2 columns]

In [64]:
# Combining the duration data into data_table
Date_Final = pd.merge(Date_cleaned, Duration_Minutes, on='UNIQUE_ORDER_NUMBER', how='left')
Date_Final

UNIQUE_ORDER_NUMBER           DATE_TIME  YEAR  QUARTER  MONTH  \
0              2017-07055448 2017-06-30 11:22:35  2017        2      6   
1              2017-07055448 2017-06-30 12:04:50  2017        2      6   
2              2017-07055448 2017-06-30 12:04:51  2017        2      6   
3              2017-07055448 2017-06-30 12:05:02  2017        2      6   
4              2017-07055448 2017-06-30 12:05:12  2017        2      6   
...                      ...                 ...   ...      ...    ...   
33374099       2016-18547561 2016-12-30 16:21:00  2016        4     12   
33374100       2016-06108542 2016-12-30 16:29:13  2016        4     12   
33374101       2016-06108542 2016-12-30 16:29:21  2016        4     12   
33374102       2016-06108542 2016-12-30 16:29:27  2016        4     12   
33374103       2016-06108542 2016-12-30 16:29:35  2016        4     12   

         DAY_OF_WEEK  DAY_OF_MONTH      TIME  DURATION_MINUTES  
0             Friday            30  11:22:35        153.883333  
1             Friday            30  12:04:50        153.883333  
2             Friday            30  12:04:51        153.883333  
3             Friday            30  12:05:02        153.883333  
4             Friday            30  12:05:12        153.883333  
...              ...           ...       ...               ...  
33374099      Friday            30  16:21:00          0.000000  
33374100      Friday            30  16:29:13        193.866667  
33374101      Friday            30  16:29:21        193.866667  
33374102      Friday            30  16:29:27        193.866667  
33374103      Friday            30  16:29:35        193.866667  

[33374104 rows x 9 columns]

In [65]:
# Date_Final.to_csv(r"C:\Users\HayateSato\Documents\OBETA\Date_Final.csv")

## Fact Table

In [66]:
Fact_only = pickDF_cleaned[["SKU", "WAREHOUSE_SECTION", "DATE_TIME", "UNIQUE_ORDER_NUMBER", "PICK_VOLUME", "QUANTITY_UNIT", "ORIGIN"]]
Fact_only_copy = Fact_only.copy()
Fact_only_copy

SKU WAREHOUSE_SECTION           DATE_TIME UNIQUE_ORDER_NUMBER  \
0         000002               SHL 2017-06-30 11:22:35       2017-07055448   
1         000002               SHL 2017-06-30 12:04:50       2017-07055448   
2         000002               SHL 2017-06-30 12:04:51       2017-07055448   
3         000002               SHL 2017-06-30 12:05:02       2017-07055448   
4         000002               SHL 2017-06-30 12:05:12       2017-07055448   
...          ...               ...                 ...                 ...   
33888980  129914        Kabellager 2016-12-30 16:21:00       2016-18547561   
33888981  189976        Kabellager 2016-12-30 16:29:13       2016-06108542   
33888982  189976        Kabellager 2016-12-30 16:29:21       2016-06108542   
33888983  189976        Kabellager 2016-12-30 16:29:27       2016-06108542   
33888984  189976        Kabellager 2016-12-30 16:29:35       2016-06108542   

          PICK_VOLUME QUANTITY_UNIT  ORIGIN  
0                  30            St      48  
1                  30            St      48  
2                  20            St      48  
3                  30            St      48  
4                  12            St      48  
...               ...           ...     ...  
33888980            2            Mt      48  
33888981           30            Mt      48  
33888982           30            Mt      48  
33888983           30            Mt      48  
33888984           30            Mt      48  

[33374104 rows x 7 columns]

In [67]:
Fact_only_copy['SKU_COUNT'] = Fact_only_copy.groupby(['UNIQUE_ORDER_NUMBER', 'SKU'])['SKU'].transform('count')
Fact_cleaned = Fact_only_copy
Fact_cleaned

SKU WAREHOUSE_SECTION           DATE_TIME UNIQUE_ORDER_NUMBER  \
0         000002               SHL 2017-06-30 11:22:35       2017-07055448   
1         000002               SHL 2017-06-30 12:04:50       2017-07055448   
2         000002               SHL 2017-06-30 12:04:51       2017-07055448   
3         000002               SHL 2017-06-30 12:05:02       2017-07055448   
4         000002               SHL 2017-06-30 12:05:12       2017-07055448   
...          ...               ...                 ...                 ...   
33888980  129914        Kabellager 2016-12-30 16:21:00       2016-18547561   
33888981  189976        Kabellager 2016-12-30 16:29:13       2016-06108542   
33888982  189976        Kabellager 2016-12-30 16:29:21       2016-06108542   
33888983  189976        Kabellager 2016-12-30 16:29:27       2016-06108542   
33888984  189976        Kabellager 2016-12-30 16:29:35       2016-06108542   

          PICK_VOLUME QUANTITY_UNIT  ORIGIN  SKU_COUNT  
0                  30            St      48         22  
1                  30            St      48         22  
2                  20            St      48         22  
3                  30            St      48         22  
4                  12            St      48         22  
...               ...           ...     ...        ...  
33888980            2            Mt      48          1  
33888981           30            Mt      48          4  
33888982           30            Mt      48          4  
33888983           30            Mt      48          4  
33888984           30            Mt      48          4  

[33374104 rows x 8 columns]

# Additional Caluclation for KPI

## Frequently Ordered SKU Pairs

In [68]:
grouped_orders_unique = Fact_only_copy.groupby('UNIQUE_ORDER_NUMBER')['SKU'].apply(set)

# Initialize an empty dictionary to count pairs of products
product_pairs_count = {}

for order_set in grouped_orders_unique:
    order = list(order_set)
    for i in range(len(order) - 1):
        pair = (order[i], order[i+1])  # Create a pair of consecutive products
        product_pairs_count[pair] = product_pairs_count.get(pair, 0) + 1

# Sort the product pairs by frequency
sorted_pairs = sorted(product_pairs_count.items(), key=lambda x: x[1], reverse=True)

result_df = pd.DataFrame(sorted_pairs, columns=['Product_Pair', 'Frequency_Count'])

#Storing SKU pairs in separate columns
result_df[['SKU_Pair1', 'SKU_Pair2']] = pd.DataFrame(result_df['Product_Pair'].tolist())

#dropping Product_pair column
result_df.drop('Product_Pair', axis=1, inplace=True)  #Use for heatmap

df_sorted = result_df.sort_values(by='Frequency_Count', ascending=False)

#We only require the top 50 most frequently ordered SKU pairs for our analysis
relevant_df = df_sorted.head(50)

#Getting a list of Warehouse sections grouped by SKUs
#This tells us all the Warehouse sections that store a particular SKU.
wh_sku = Fact_only_copy.groupby('SKU')['WAREHOUSE_SECTION'].apply(lambda x: ', '.join(sorted(set(x)))).reset_index()
wh_sku.columns = ['SKU_LIST', 'WH_SECTION']

#Joining the wh_sku DF with releavnt DFs to see if most frequently ordered SKU pairs are stored in the same 
#Warehouse sections or not. If not, then suggestion for OBETA to change the layout to optimize their WHs. 

DF = relevant_df.set_index('SKU_Pair1').join(wh_sku.set_index('SKU_LIST'), how='left')
DF.rename(columns={'WH_SECTION': 'WH_SKU1'}, inplace=True)

#Joining resultDF with warehouses to get the warehouse sections for SKU_Pair1
SKU_pair = DF.join(wh_sku.set_index('SKU_LIST'), on='SKU_Pair2', how='left')
SKU_pair.rename(columns={'WH_SECTION': 'WH_SKU2'}, inplace=True)
SKU_pair.reset_index(inplace=True)
SKU_pair

SKU_Pair1  Frequency_Count SKU_Pair2                   WH_SKU1  \
0     104076             5188    109910              HRL, Manuell   
1     104131            12009    109910  HRL, Kabellager, Manuell   
2     104131             7616    109905  HRL, Kabellager, Manuell   
3     104131             4682    104076  HRL, Kabellager, Manuell   
4     104131             3774    104101  HRL, Kabellager, Manuell   
5     104261             6929    104270       Kabellager, Manuell   
6     104261             3907    104251       Kabellager, Manuell   
7     104270             2834    104251       Kabellager, Manuell   
8     109910            14248    104131  HRL, Kabellager, Manuell   
9     109910            14037    109905  HRL, Kabellager, Manuell   
10    109910             4700    104130  HRL, Kabellager, Manuell   
11    109910             2701    231906  HRL, Kabellager, Manuell   
12    150521             3877    S16996             AKL, HRL, SHL   
13    171862             2796    171920             AKL, HRL, SHL   
14    171864             4265    171922                       HRL   
15    189919             2868    189920           HRL, Kabellager   
16    202853             4059    202854                   Manuell   
17    231906             2714    V31971              HRL, Manuell   
18    234114            12702    234112             AKL, HRL, SHL   
19    234141             6097    234142             AKL, HRL, SHL   
20    239832             2906    202853             AKL, HRL, SHL   
21    244372             4034    243083             AKL, HRL, SHL   
22    244397             2732    244371             AKL, HRL, SHL   
23    250212             5367    253295             AKL, HRL, SHL   
24    253035             3033    253278             AKL, HRL, SHL   
25    253295            11315    253410             AKL, HRL, SHL   
26    253411             2836    D64148             AKL, HRL, SHL   
27    256649             3207    256624             AKL, HRL, SHL   
28    258502             4554    258506             AKL, HRL, SHL   
29    272932             3412    272930                  AKL, SHL   
30    C06539             3589    C06472             AKL, HRL, SHL   
31    D64148             2794    D64230             AKL, HRL, SHL   
32    D64155             4043    253410             AKL, HRL, SHL   
33    F23723             2721    F23724             AKL, HRL, SHL   
34    F80853             3222    H40570             AKL, HRL, SHL   
35    G41650             5369    G41816             AKL, HRL, SHL   
36    G41658             5591    G41650             AKL, HRL, SHL   
37    G41665             2770    G41650             AKL, HRL, SHL   
38    G41669             2670    243607             AKL, HRL, SHL   
39    G41816             7648    110980             AKL, HRL, SHL   
40    H48638             3750    T95038             AKL, HRL, SHL   
41    H48662             3029    H48638             AKL, HRL, SHL   
42    H83153             5019    D64155             AKL, HRL, SHL   
43    H83162             3717    H83143             AKL, HRL, SHL   
44    J45588             3449    J45435             AKL, HRL, SHL   
45    J45738             2893    J45430             AKL, HRL, SHL   
46    V68352             3125    V68445             AKL, HRL, SHL   
47    V68356             6258    V68446             AKL, HRL, SHL   
48    V68359             3099    V68356             AKL, HRL, SHL   
49    V68397             3805    V68352             AKL, HRL, SHL   

                     WH_SKU2  
0   HRL, Kabellager, Manuell  
1   HRL, Kabellager, Manuell  
2   HRL, Kabellager, Manuell  
3               HRL, Manuell  
4   HRL, Kabellager, Manuell  
5        Kabellager, Manuell  
6        Kabellager, Manuell  
7        Kabellager, Manuell  
8   HRL, Kabellager, Manuell  
9   HRL, Kabellager, Manuell  
10           HRL, Kabellager  
11              HRL, Manuell  
12             AKL, HRL, SHL  
13             AKL, HRL, SHL  
14                

## SKU Order Inefficiency 

In [69]:
myDF = pickDF_cleaned
myDF['SKU_COUNT'] = myDF.groupby(['UNIQUE_ORDER_NUMBER', 'SKU'])['SKU'].transform('count')
#Filter those records where sku count > 1
orders_with_duplicate_sku = myDF[myDF['SKU_COUNT'] > 1]

inefficient_orders_count = orders_with_duplicate_sku.groupby(['YEAR','QUARTER','MONTH','WAREHOUSE_SECTION'])['ORDER_NUMBER'].nunique().reset_index()
inefficient_orders_count.rename(columns={'ORDER_NUMBER': 'INEFFICIENT_ORDERS_COUNT'}, inplace=True)
display(inefficient_orders_count)

#contains the count of unique order numbers for each warehouse section
orders_per_WH = pickDF_cleaned.groupby(['YEAR','QUARTER', 'MONTH', 'WAREHOUSE_SECTION'])['ORDER_NUMBER'].nunique().reset_index()
orders_per_WH.rename(columns={'ORDER_NUMBER': 'TOTAL_ORDERS_PLACED'}, inplace=True)
display(orders_per_WH)

YEAR  QUARTER  MONTH WAREHOUSE_SECTION  INEFFICIENT_ORDERS_COUNT
0    2011        2      6               AKL                      2740
1    2011        2      6               HRL                       407
2    2011        2      6        Kabellager                       153
3    2011        2      6           Manuell                        83
4    2011        3      7               AKL                      9331
..    ...      ...    ...               ...                       ...
494  2020        3      7               AKL                       826
495  2020        3      7               HRL                       772
496  2020        3      7        Kabellager                       399
497  2020        3      7           Manuell                       276
498  2020        3      7               SHL                      3783

[499 rows x 5 columns]

YEAR  QUARTER  MONTH WAREHOUSE_SECTION  TOTAL_ORDERS_PLACED
0    2011        2      6               AKL                15030
1    2011        2      6               HRL                 6690
2    2011        2      6        Kabellager                 1646
3    2011        2      6           Manuell                 3409
4    2011        3      7               AKL                49436
..    ...      ...    ...               ...                  ...
494  2020        3      7               AKL                 4652
495  2020        3      7               HRL                10283
496  2020        3      7        Kabellager                 6726
497  2020        3      7           Manuell                 6753
498  2020        3      7               SHL                34352

[499 rows x 5 columns]

In [70]:
#left join with orders_per_WH
#This will bring TOTAL_ORDERS_PLACED, INEFFICIENT_ORDERS_COUNT together so we can get a monthly percentage

inefficient_orders = pd.merge(orders_per_WH, inefficient_orders_count, on=['YEAR','QUARTER', 'MONTH','WAREHOUSE_SECTION'], how='left')
inefficient_orders['PERCENT_INEFFICIENCY'] = (inefficient_orders['INEFFICIENT_ORDERS_COUNT'] / inefficient_orders['TOTAL_ORDERS_PLACED']) * 100
inefficient_orders

YEAR  QUARTER  MONTH WAREHOUSE_SECTION  TOTAL_ORDERS_PLACED  \
0    2011        2      6               AKL                15030   
1    2011        2      6               HRL                 6690   
2    2011        2      6        Kabellager                 1646   
3    2011        2      6           Manuell                 3409   
4    2011        3      7               AKL                49436   
..    ...      ...    ...               ...                  ...   
494  2020        3      7               AKL                 4652   
495  2020        3      7               HRL                10283   
496  2020        3      7        Kabellager                 6726   
497  2020        3      7           Manuell                 6753   
498  2020        3      7               SHL                34352   

     INEFFICIENT_ORDERS_COUNT  PERCENT_INEFFICIENCY  
0                        2740             18.230206  
1                         407              6.083707  
2                         153              9.295261  
3                          83              2.434732  
4                        9331             18.874909  
..                        ...                   ...  
494                       826             17.755804  
495                       772              7.507537  
496                       399              5.932203  
497                       276              4.087072  
498                      3783             11.012459  

[499 rows x 7 columns]

# Loading to mySQL

In [71]:
# Checking SQL connection
try: 
    conn = pymysql.connect(host = db_host,
                          port = int(3306),
                          user = "root",
                          passwd = db_password,
                          db = db_name_prod)
    print("sucess")
except e:
    print("error")

sucess


## Standaloble Table to mySQL

In [72]:
# Create a connection to the MySQL server
connection = mysql.connector.connect(host=db_host, user=db_username, password=db_password, port='3306', database=db_name_prod, connect_timeout=120)
# Create a cursor object to execute SQL queries
cursor = connection.cursor()
# Create the table (if it doesn't exist)
create_table_query = '''
CREATE TABLE IF NOT EXISTS Standalone_Table (
    UNIQUE_ORDER_NUMBER VARCHAR(255),
    ORDER_POSITION VARCHAR(255)
)
'''
cursor.execute(create_table_query)
# Convert DataFrame to a list of tuples for inserting into MySQL
data = [tuple(row) for row in Standalone_Table.itertuples(index=False)]
# Insert DataFrame data into MySQL table
insert_query = f'INSERT INTO Standalone_Table (UNIQUE_ORDER_NUMBER, ORDER_POSITION) VALUES (%s, %s)'

chunk_size = 1000
for i in range(0, len(data), chunk_size):
    chunk = data[i:i + chunk_size]
    try:
        cursor.executemany(insert_query, chunk)
        connection.commit()
        print(f"Inserted {len(chunk)} rows successfully.")
    except Error as e:
        # Handle errors and potentially retry the chunk
        print(f"Error: {e}")
        connection.rollback()
# Close the cursor and connection
cursor.close()
connection.close()
print("Connection closed.")

Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1

## Product Table to mySQL

In [73]:
# Create a connection to the MySQL server
connection = mysql.connector.connect(host=db_host, user=db_username, password=db_password, port='3306', database=db_name_prod, connect_timeout=120)
# Create a cursor object to execute SQL queries
cursor = connection.cursor()
# Create the table (if it doesn't exist)
create_table_query = '''
CREATE TABLE IF NOT EXISTS product_table (
    SKU VARCHAR(255),
    DESCRIPTION VARCHAR(255),
    PRODUCT_GROUP VARCHAR(255)
    
)
'''
cursor.execute(create_table_query)
# Convert DataFrame to a list of tuples for inserting into MySQL
data = [tuple(row) for row in productDF_cleaned.itertuples(index=False)]
# Insert DataFrame data into MySQL table
insert_query = f'INSERT INTO product_table (SKU, DESCRIPTION, PRODUCT_GROUP) VALUES (%s, %s, %s)'

chunk_size = 1000
for i in range(0, len(data), chunk_size):
    chunk = data[i:i + chunk_size]
    try:
        cursor.executemany(insert_query, chunk)
        connection.commit()
        print(f"Inserted {len(chunk)} rows successfully.")
    except Error as e:
        # Handle errors and potentially retry the chunk
        print(f"Error: {e}")
        connection.rollback()
# Close the cursor and connection
cursor.close()
connection.close()
print("Connection closed.")

Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1

## Date Table to mySQL

In [74]:
# Create a connection to the MySQL server
connection = mysql.connector.connect(host=db_host, user=db_username, password=db_password, port='3306', database=db_name_prod, connect_timeout=120)
# Create a cursor object to execute SQL queries
cursor = connection.cursor()
# Create the table (if it doesn't exist)
create_table_query = '''
CREATE TABLE IF NOT EXISTS Date_Final (
    DATE_TIME DATE,
    UNIQUE_ORDER_NUMBER VARCHAR(255),
    YEAR DATE,
    QUARTER INT,
    MONTH INT,
    DAY_OF_WEEK VARCHAR(255),
    DAY_OF_MONTH INT,
    TIME DATE,
    Duration_Minutes FLOAT
    
)
'''
cursor.execute(create_table_query)
# Convert DataFrame to a list of tuples for inserting into MySQL
data = [tuple(row) for row in Date_Final.itertuples(index=False)]
# Insert DataFrame data into MySQL table
insert_query = f'INSERT INTO Date_Final(UNIQUE_ORDER_NUMBER, DATE_TIME, YEAR, QUARTER, MONTH, DAY_OF_WEEK, DAY_OF_MONTH, TIME, Duration_Minutes) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s)'

chunk_size = 1000
for i in range(0, len(data), chunk_size):
    chunk = data[i:i + chunk_size]
    try:
        cursor.executemany(insert_query, chunk)
        connection.commit()
        print(f"Inserted {len(chunk)} rows successfully.")
    except Error as e:
        # Handle errors and potentially retry the chunk
        print(f"Error: {e}")
        connection.rollback()
# Close the cursor and connection
cursor.close()
connection.close()
print("Connection closed.")

Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1

## Fact Table to mySQL

In [75]:
# Create a connection to the MySQL server
connection = mysql.connector.connect(host=db_host, user=db_username, password=db_password, port='3306', database=db_name_prod, connect_timeout=120)
# Create a cursor object to execute SQL queries
cursor = connection.cursor()
# Create the table (if it doesn't exist)
create_table_query = '''
CREATE TABLE IF NOT EXISTS Fact_cleaned (
    SKU VARCHAR(255),
    WAREHOUSE_SECTION VARCHAR(255),
    UNIQUE_ORDER_NUMBER VARCHAR(255),
    PICK_VOLUME INT,
    QUANTITY_UNIT VARCHAR(255),
    ORIGIN INT,
    DATE_TIME DATE,
    SKU_COUNT INT
    
)
'''
cursor.execute(create_table_query)
# Convert DataFrame to a list of tuples for inserting into MySQL
data = [tuple(row) for row in Fact_cleaned.itertuples(index=False)]
# Insert DataFrame data into MySQL table
insert_query = f'INSERT INTO Fact_cleaned (SKU, WAREHOUSE_SECTION, UNIQUE_ORDER_NUMBER, PICK_VOLUME, QUANTITY_UNIT, ORIGIN,  DATE_TIME,  SKU_COUNT) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)'

chunk_size = 1000
for i in range(0, len(data), chunk_size):
    chunk = data[i:i + chunk_size]
    try:
        cursor.executemany(insert_query, chunk)
        connection.commit()
        print(f"Inserted {len(chunk)} rows successfully.")
    except Error as e:
        # Handle errors and potentially retry the chunk
        print(f"Error: {e}")
        connection.rollback()
# Close the cursor and connection
cursor.close()
connection.close()
print("Connection closed.")

Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1000 rows successfully.
Inserted 1

## FrequentlyOrderedPairs Table to MySQL

In [78]:
# Create a connection to the MySQL server
connection = mysql.connector.connect(host=db_host, user=db_username, password=db_password, port='3306', database=db_name_prod, connect_timeout=120)
# Create a cursor object to execute SQL queries
cursor = connection.cursor()
# Create the table (if it doesn't exist)
create_table_query = '''
CREATE TABLE IF NOT EXISTS SKU_pair (
    SKU_Pair1 VARCHAR(255),
    Frequency_Count INT,
    SKU_Pair2 VARCHAR(255),
    WH_SKU1 VARCHAR (255),
    WH_SKU2 VARCHAR(255)
    
)
'''
cursor.execute(create_table_query)
# Convert DataFrame to a list of tuples for inserting into MySQL
data = [tuple(row) for row in SKU_pair.itertuples(index=False)]
# Insert DataFrame data into MySQL table
insert_query = f'INSERT INTO SKU_pair (SKU_Pair1, Frequency_Count, SKU_Pair2, WH_SKU1, WH_SKU2) VALUES (%s, %s, %s, %s, %s)'

chunk_size = 1000
for i in range(0, len(data), chunk_size):
    chunk = data[i:i + chunk_size]
    try:
        cursor.executemany(insert_query, chunk)
        connection.commit()
        print(f"Inserted {len(chunk)} rows successfully.")
    except Error as e:
        # Handle errors and potentially retry the chunk
        print(f"Error: {e}")
        connection.rollback()
# Close the cursor and connection
cursor.close()
connection.close()
print("Connection closed.")

Inserted 50 rows successfully.
Connection closed.


## SKUInefficiency Table to MySQL

In [79]:
# Create a connection to the MySQL server
connection = mysql.connector.connect(host=db_host, user=db_username, password=db_password, port='3306', database=db_name_prod, connect_timeout=120)
# Create a cursor object to execute SQL queries
cursor = connection.cursor()
# Create the table (if it doesn't exist)
create_table_query = '''
CREATE TABLE IF NOT EXISTS inefficient_orders (
    YEAR VARCHAR(255),
    QUARTER VARCHAR(255),
    MONTH VARCHAR(255),
    WAREHOUSE_SECTION VARCHAR(255),
    TOTAL_ORDERS_PLACED INT,
    INEFFICIENT_ORDERS_COUNT INT,
    PERCENT_INEFFICIENCY FLOAT
    
)
'''
cursor.execute(create_table_query)
# Convert DataFrame to a list of tuples for inserting into MySQL
data = [tuple(row) for row in inefficient_orders.itertuples(index=False)]
# Insert DataFrame data into MySQL table
insert_query = f'INSERT INTO inefficient_orders (YEAR, QUARTER, MONTH, WAREHOUSE_SECTION, TOTAL_ORDERS_PLACED, INEFFICIENT_ORDERS_COUNT, PERCENT_INEFFICIENCY) VALUES (%s, %s, %s, %s, %s, %s, %s)'

chunk_size = 1000
for i in range(0, len(data), chunk_size):
    chunk = data[i:i + chunk_size]
    try:
        cursor.executemany(insert_query, chunk)
        connection.commit()
        print(f"Inserted {len(chunk)} rows successfully.")
    except Error as e:
        # Handle errors and potentially retry the chunk
        print(f"Error: {e}")
        connection.rollback()
# Close the cursor and connection
cursor.close()
connection.close()
print("Connection closed.")

Inserted 499 rows successfully.
Connection closed.
